In [28]:

import tifffile
import numpy as np
import os
# import cv2

import gc
import json
import time
import pandas as pd
# import SimpleITK as sitk
import seaborn as sns

from scipy import stats
from scipy.ndimage import zoom
import scipy.ndimage as ndi

%matplotlib inline
import matplotlib.pyplot as plt

from multiprocessing import Pool
plt.gray()

import json, os.path, os, re, time
import joblib
import subprocess as sp
import nibabel as nib
import scipy.spatial


<Figure size 640x480 with 0 Axes>

In [29]:

"""Analytic Cosinor Test Module

This module provides functions for detecting rhythmic patterns in time-series data 
using analytic cosinor testing. The primary functionality calculates the maximum 
Pearson correlation between input data and sine/cosine waves of a specified period,
along with statistical significance testing.

The module implements the analytic cosinor test which:
1. Generates normalized orthogonal sine and cosine basis vectors
2. Calculates the maximum correlation between input data and these basis vectors
3. Computes p-values for statistical significance
4. Optionally adjusts for standard error of the mean (SEM)

Main Functions:
    costest: Performs analytic cosinor test on a single time-series vector
    batch_costest: Vectorized version for processing multiple time-series at once

The method is particularly useful for detecting circadian or other periodic patterns
in biological and time-series data.

Author: ygriku
License: See LICENSE file
"""

import numpy as np

# Generate normalized orthogonal basis vectors
def _norm_bases(n_tp, n_tp_in_per):
    """Generate normalized sine and cosine basis vectors for correlation analysis.
    
    Args:
        n_tp (int): Total number of time points in the data
        n_tp_in_per (float): Number of time points in one period
        
    Returns:
        tuple: (normalized_sine_wave, normalized_cosine_wave) - orthogonal basis vectors
    """
    base_s = np.sin(np.arange(n_tp)/n_tp_in_per*2*np.pi)
    base_c = np.cos(np.arange(n_tp)/n_tp_in_per*2*np.pi)
    base_s_m = base_s - np.mean(base_s)
    base_c_m = base_c - np.mean(base_c)
    norm_base_s = (base_s_m)/np.sqrt(np.sum((base_s_m)*(base_s_m)))
    norm_base_c = (base_c_m)/np.sqrt(np.sum((base_c_m)*(base_c_m)))
    return norm_base_s, norm_base_c


# Calculate maximum correlation between input vector and basis vectors
def _calc_max_corr(vec, norm_base_s, norm_base_c):
    """Calculate the maximum correlation between an input vector and sine/cosine basis vectors.
    
    Args:
        vec (array): Input time-series vector
        norm_base_s (array): Normalized sine basis vector
        norm_base_c (array): Normalized cosine basis vector
        
    Returns:
        tuple: (max_correlation_value, phase_of_max_correlation) in radians
    """
    vec_m = vec - np.mean(vec)
    norm_vec = (vec_m)/np.sqrt(np.sum((vec_m)*(vec_m)))
    max_corr_value = np.sqrt(np.power(np.dot(norm_base_c, norm_vec), 2) + np.power(np.dot(norm_base_s, norm_vec), 2))
    # Ensure the maximum correlation does not exceed 1 due to possible numerical subtleties
    max_corr_value = min(1.0, max_corr_value)
    max_corr_phase = np.arctan2(np.dot(norm_base_s, norm_vec), np.dot(norm_base_c, norm_vec))
    return max_corr_value, max_corr_phase


# Calculate p-value for maximum correlation
def _max_corr_pval(num_datapoints, max_corr):
    """Calculate the p-value for the maximum Pearson correlation.
    
    Args:
        num_datapoints (int): Number of data points in the time series
        max_corr (float): Maximum correlation value
        
    Returns:
        float: P-value (probability under null hypothesis)
    """
    n = num_datapoints - 3
    p = np.power((1 - np.power(max_corr, 2)), n / 2)
    return p


# Calculate the SEM adjustment ratio
def _sem_ratio(avg_vector, sem_vector, alpha):
    """Calculate the ratio for adjusting correlation based on standard error of the mean.
    
    This function computes how much the correlation should be adjusted based on the
    confidence interval defined by the SEM values, using a 95% confidence level.
    
    Args:
        avg_vector (array): Average values at each time point
        sem_vector (array): Standard error of the mean values at each time point
        
    Returns:
        float: Adjustment ratio (0.0 to 1.0) for the correlation value
    """
    a_vec = avg_vector - np.mean(avg_vector)
    ratio = 1.0 - alpha / np.sqrt(np.sum(np.power(a_vec / sem_vector, 2))) # 0.67 is the 50% confidence interval
    return max(0, ratio)


# Main function for the analytic cosinor test
def costest(avg_vec, n_tp_in_per, sem_vec=None):
    """Perform analytic cosinor test on a time-series vector.
    
    Calculates the maximum Pearson correlation between the input vector and 
    sine/cosine curves with the specified period, along with statistical significance.
    
    Args:
        avg_vec (array): Vector of averaged values at each time point
        n_tp_in_per (float): Number of time points in one period
        sem_vec (array, optional): Vector of standard error of the mean values 
                                  at each time point
    
    Returns:
        tuple: (max_correlation, phase_radians, original_p_value, sem_adjusted_p_value)
            - max_correlation (float): Maximum correlation value
            - phase_radians (float): Phase in radians of the maximum correlation
            - original_p_value (float): Original p-value
            - sem_adjusted_p_value (float): SEM-adjusted p-value
    """
    # Get the number of time points in the data
    n_tp = len(avg_vec)

    # prepare bases
    norm_base_s, norm_base_c = _norm_bases(n_tp, n_tp_in_per)

    # prepare vector to handle nan
    avg_vector = avg_vec.copy()

    # replace nan in AVG with median
    avg_vector[np.isnan(avg_vector)] = np.nanmedian(avg_vector)

    if sem_vec is not None:
        ## prepare vector to handle nan
        sem_vector = sem_vec.copy()

        # each SEM needs to be >0
        sem_vector[~(sem_vector>0)] = np.nanmax(sem_vector)
        # replace nan in SEM with an effectively infinite SEM for missing averages
        sem_vector[np.isnan(avg_vector)] = np.nanmax(sem_vector)*1000000
        # taking the SEM into account
        sem_r = _sem_ratio(avg_vector, sem_vector, alpha)
    else:
        # if no SEM is provided, sem_r is set to 1.0
        sem_r = 1.0

    # tuple of max-correlation value and the phase of max correlation
    mc, mc_ph = _calc_max_corr(avg_vector, norm_base_s, norm_base_c)

    adj_mc = mc * sem_r
    p_org = _max_corr_pval(n_tp, mc)
    p_sem_adj = _max_corr_pval(n_tp, adj_mc)
    
    # max-correlation value, phase of max correlation, original p, SEM adjusted p
    return mc, mc_ph, p_org, p_sem_adj


# Vectorized batch version of the costest function
def batch_costest(avg_vec_matrix, n_tp_in_per, sem_vec_matrix=None, alpha=0.67):
    """Perform analytic cosinor test on multiple time-series vectors.
    
    Calculates the maximum Pearson correlation between each input vector and 
    sine/cosine curves with the specified period, along with statistical significance.
    This vectorized implementation is more efficient for processing large datasets.

    Args:
        avg_vec_matrix (array): 2D array where each row is a vector of averaged 
                               values at each time point
        n_tp_in_per (float): Number of time points in one period
        sem_vec_matrix (array, optional): 2D array where each row is a vector of 
                                         standard error of the mean values at each time point

    Returns:
        ndarray: Array with shape (n_vectors, 4) containing for each input vector:
            - Column 0: Maximum correlation value
            - Column 1: Phase in radians of the maximum correlation
            - Column 2: Original p-value
            - Column 3: SEM-adjusted p-value
    """
    # Convert to numpy array if not already
    avg_vec_matrix = np.asarray(avg_vec_matrix)
    n_vectors, n_tp = avg_vec_matrix.shape

    # prepare bases once
    norm_base_s, norm_base_c = _norm_bases(n_tp, n_tp_in_per)

    # Vectorized NaN handling for avg_vec_matrix
    avg_matrix_clean = avg_vec_matrix.copy()
    nan_mask = np.isnan(avg_matrix_clean)
    # Replace NaN with median for each row
    for i in range(n_vectors):
        if np.any(nan_mask[i]):
            avg_matrix_clean[i, nan_mask[i]] = np.nanmedian(avg_matrix_clean[i])

    # Vectorized correlation calculation
    # Center the data
    avg_means = np.mean(avg_matrix_clean, axis=1, keepdims=True)
    avg_centered = avg_matrix_clean - avg_means
    
    # Normalize the vectors
    avg_norms = np.sqrt(np.sum(avg_centered**2, axis=1, keepdims=True))
    norm_avg = avg_centered / avg_norms
    
    # Calculate correlations with sine and cosine bases
    corr_s = np.dot(norm_avg, norm_base_s)
    corr_c = np.dot(norm_avg, norm_base_c)
    
    # Calculate max correlation and phase
    mc_array = np.sqrt(corr_s**2 + corr_c**2)
    mc_array = np.minimum(mc_array, 1.0)  # Ensure max correlation doesn't exceed 1
    mc_ph_array = np.arctan2(corr_s, corr_c)
    
    # Calculate original p-values vectorized
    p_org_array = np.power((1 - mc_array**2), (n_tp - 3) / 2)
    
    # Handle SEM adjustments vectorized
    sem_r_array = np.ones(n_vectors)
    if sem_vec_matrix is not None:
        sem_vec_matrix = np.asarray(sem_vec_matrix)
        sem_matrix_clean = sem_vec_matrix.copy()
        
        # Vectorized SEM handling
        sem_nonpositive = ~(sem_matrix_clean > 0)
        sem_nan = np.isnan(sem_matrix_clean)
        
        # Replace non-positive and NaN values
        for i in range(n_vectors):
            sem_max = np.nanmax(sem_matrix_clean[i])
            sem_matrix_clean[i, sem_nonpositive[i]] = sem_max
            sem_matrix_clean[i, sem_nan[i]] = sem_max * 1000000
            
            # Calculate SEM ratio
            ratio_vec = avg_centered[i] / sem_matrix_clean[i]
            sem_r_array[i] = max(0, 1.0 - alpha / np.sqrt(np.sum(ratio_vec**2)))
    
    # Calculate SEM-adjusted correlations and p-values
    adj_mc_array = mc_array * sem_r_array
    p_sem_adj_array = np.power((1 - adj_mc_array**2), (n_tp - 3) / 2)

    return np.column_stack([mc_array, mc_ph_array, p_org_array, p_sem_adj_array])

    

class mapping_to_atlas():
    def __init__(self,data_atlas_path, ants_dir_name, data_ants_path, before_ants_file):
        self.ants_voxel_unit = Resize_um
        self.original_voxel_unit = Resize_um
        self.img_voxel_unit = Resize_um

        
        self.atlas_tif_path = data_atlas_path
        self.atlas_nii_path = self.atlas_tif_path.replace(".tif",".nii.gz")
        
        #for image size check
        
        
#         self.flip_tif_path =  os.path.join(data_parent_path,"{}/{}/ANTs/density_img_50um_flip.tif".format(organ_name,sample_name))
#         self.flip_txt_path = os.path.join(data_parent_path,"{}/{}/ANTs/flip_memo.txt".format(organ_name,sample_name))

        self.ants_dst_dir = os.path.join(data_ants_path, ants_dir_name+"/")
    
        self.sample_resize_img_path =  os.path.join(data_ants_path,before_ants_file)
        
        #self.flip_tif_path --->  self.sample_nii_path
        self.sample_nii_path = os.path.join(data_ants_path ,before_ants_file.replace(".tif",".nii.gz"))
        
        self.before_ants_np_path = os.path.join(data_ants_path,"all_points_um.npy")
        
        if not os.path.exists(self.ants_dst_dir):
            print("make ants folder {}".format(self.ants_dst_dir))
            os.makedirs(self.ants_dst_dir)
        else:
            print("{} already exists".format(self.ants_dst_dir))

        self.moving_nii_path = self.sample_nii_path
        
        self.output_nii_path = os.path.join(self.ants_dst_dir, "after_ants.nii.gz")
        
        self.prefix_ants ="/opt/ANTs/bin/"# "/usr/local/ANTs/"
        
#         self.moving_points_path = os.path.join(self.ants_dst_dir,"moving.csv")   #?
#         self.moved_points_path = os.path.join(self.ants_dst_dir,"moved.csv")#?
#         self.moved_denstity_path = os.path.join(self.ants_dst_dir,"moved_denstity.tif")
    
        
    def tif2nii(self, tif_path, nii_path, nii_voxel_unit):
        tif_img = tifffile.imread(tif_path)
#         nii_img = nib.Nifti1Image(np.swapaxes(tif_img,0,2), affine=None)
        nii_img = nib.Nifti1Image(tif_img, affine=None)
        aff = np.diag([-nii_voxel_unit,-nii_voxel_unit,nii_voxel_unit,1])
        nii_img.header.set_qform(aff, code=2)
        nii_img.to_filename(nii_path)
        return



    def run_antsRegistration(self,prefix_ants, atlas_file, moving_file, dst_dir, threads):
        cmd = "ITK_GLOBAL_DEFAULT_NUMBER_OF_THREADS={THREADS} && "
        cmd += "{EXECUTABLE} -d 3 "
        cmd += "--initial-moving-transform [{ATLAS_FILE},{MOVING_FILE},1] "
        cmd += "--interpolation Linear "
        cmd += "--use-histogram-matching 0 "
        cmd += "--winsorize-image-intensities [0.05,1.0] "  
        cmd += "--float 0 "
        cmd += "--output [{DST_PREFIX},{WARPED_FILE},{INVWARPED_FILE}] "
        cmd += "--transform Affine[0.1] --metric MI[{ATLAS_FILE},{MOVING_FILE},1,128,Regular,0.5] --convergence [10000x10000x10000,1e-5,15] --shrink-factors 4x2x1 --smoothing-sigmas 2x1x0vox "
        cmd += "--transform SyN[0.1,3.0,0.0] --metric CC[{ATLAS_FILE},{MOVING_FILE},1,5] --convergence [300x100x30,1e-6,10] --shrink-factors 4x2x1 --smoothing-sigmas 2x1x0vox"

#         cmd += "--transform Affine[0.1] --metric MI[{ATLAS_FILE},{MOVING_FILE},1,128,Regular,0.5] --convergence [10000x10000x10000,1e-5,15] --shrink-factors 8x4x2 --smoothing-sigmas 3x2x1vox "
#         cmd += "--transform SyN[0.1,3.0,0.0] --metric CC[{ATLAS_FILE},{MOVING_FILE},1,4] --convergence [500x500x500x50,1e-6,10] --shrink-factors 8x4x2x1 --smoothing-sigmas 3x2x1x0vox"
        cmd = cmd.format(
            THREADS = threads,
            EXECUTABLE = os.path.join(prefix_ants, "antsRegistration"),
            DST_PREFIX = os.path.join(dst_dir, "F2M_"),
            WARPED_FILE = os.path.join(dst_dir, "F2M_Warped.nii.gz"),
            INVWARPED_FILE = os.path.join(dst_dir, "F2M_InvWarped.nii.gz"),
            ATLAS_FILE = atlas_file,
            MOVING_FILE = moving_file,
        )
        print("[*] Executing : {}".format(cmd))
        sp.call(cmd, shell=True)
        return


    #def set_
    
    #scale of list is atlas_voxel_unit
    def make_density_image(self,list_x,list_y,list_z,size_x,size_y,size_z):
        depth,height,width = size_z,size_y,size_x
        density_img,_ = np.histogramdd(
            np.vstack([list_z,list_y,list_x]).T,
            bins=(depth, height, width),
            range=[(0,depth-1),(0,height-1),(0,width-1)]
        )
        return density_img
    
    def run_antsApplyTransformsToPoints(self, prefix_ants, src_csv, dst_csv, ANTs_image_dir):
        cmd = "{EXECUTABLE} "
        cmd += "-d 3 "
        cmd += "-i {SRC_CSV} "
        cmd += "-o {DST_CSV} "
        cmd += "-t [{AFFINE_MAT},1] "
        cmd += "-t {INVWARP_NII}"
        cmd = cmd.format(
            EXECUTABLE = os.path.join(prefix_ants, "antsApplyTransformsToPoints"),
            AFFINE_MAT = os.path.join(ANTs_image_dir, "F2M_0GenericAffine.mat"),
            INVWARP_NII = os.path.join(ANTs_image_dir, "F2M_1InverseWarp.nii.gz"),
            SRC_CSV = src_csv,
            DST_CSV = dst_csv,
        )
        #print("[*] Executing : {}".format(cmd))
        # supress output
        with open(os.devnull, 'w') as devnull:
            sp.check_call(cmd, shell=True, stdout=devnull)
        return
    
    def run_antsApplyTransforms(self, prefix_ants, src_file, atlas_file, dst_file, ANTs_image_dir):
        cmd = "{EXECUTABLE} "
        cmd += "-d 3 "
        cmd += "-e 0 "  #choose 0/1/2/3 mapping to scalar/vector/tensor/time-series
        cmd += "-i {SRC_FILE} "
        cmd += "-r {REF} "
        cmd += "-o {DST_FILE} "
        cmd += "-n {INTERP} "
        cmd += "-t {INVWARP_NII} "
        cmd += "-t {AFFINE_MAT} "
#         cmd += "-t [{AFFINE_MAT},1] "
#         cmd += "-t {INVWARP_NII} "
       
        cmd = cmd.format(
            EXECUTABLE = os.path.join(prefix_ants, "antsApplyTransforms"),
            SRC_FILE = src_file,
            REF = atlas_file,
            DST_FILE = dst_file,
            INTERP = "Linear",
            INVWARP_NII = os.path.join(ANTs_image_dir, "F2M_1Warp.nii.gz"),
            AFFINE_MAT = os.path.join(ANTs_image_dir, "F2M_0GenericAffine.mat"),
        
        )
        #print("[*] Executing : {}".format(cmd))
        # supress output
        with open(os.devnull, 'w') as devnull:
            sp.check_call(cmd, shell=True, stdout=devnull)
        return 
    
#2D slice tif images -> 3D tif image
def stack_2d_images(path):
    
    imgs = os.listdir(path)

    img0 = tifffile.imread(path + "/"+imgs[0])
    
    width = img0.shape[0]
    height  = img0.shape[1]
    
    stack_image = np.zeros((width, height, len(imgs)))
    
    for i, img_f in enumerate(imgs):
        if "ANTs" in img_f or "ANTsR" in img_f:
            continue
        img = tifffile.imread(path + "/"+img_f)
        stack_image[:,:,i]=img
    return stack_image



def convert_nii_to_tiff(nii_file, output_tiff_file):
    # NIfTI ファイルを読み込む
    nii_data = nib.load(nii_file)
    # NIfTI データを NumPy 配列に変換
    nii_array = nii_data.get_fdata()
    # NumPy 配列を TIFF ファイルに保存
    tifffile.imwrite(output_tiff_file, nii_array)

def decompress_gzip(input_file, output_file):
    with gzip.open(input_file, 'rb') as f_in:
        with open(output_file, 'wb') as f_out:
            shutil.copyfileobj(f_in, f_out)


def convolve_3d_array(data, kernel):
    # 各チャンネルに対して畳み込みを実行
    result = convolve(data, kernel, mode='same')

    return result

    
class UnionFind:
    def __init__(self, n):
        self.parent = list(range(n))
        self.rank = [1] * n

    def find(self, u):
        if u != self.parent[u]:
            self.parent[u] = self.find(self.parent[u])
        return self.parent[u]

    def union(self, u, v):
        root_u = self.find(u)
        root_v = self.find(v)
        
        if root_u != root_v:
            if self.rank[root_u] > self.rank[root_v]:
                self.parent[root_v] = root_u
            elif self.rank[root_u] < self.rank[root_v]:
                self.parent[root_u] = root_v
            else:
                self.parent[root_v] = root_u
                self.rank[root_u] += 1

def merge_lists(lists):
    # 全ての数値の最大値を求める
    max_value = max(max(lst) for lst in lists) + 1
    uf = UnionFind(max_value)
    
    # 各リスト内の要素を統合
    for lst in lists:
        first = lst[0]
        for num in lst[1:]:
            uf.union(first, num)
    
    # 各要素が属する集合を見つける
    groups = {}
    for lst in lists:
        root = uf.find(lst[0])
        if root not in groups:
            groups[root] = set()
        for num in lst:
            groups[root].add(num)
    
    # 集合をリストに変換して返す
    return [sorted(list(group)) for group in groups.values()]




from statsmodels.stats.multitest import multipletests

# calculate max correlation
# def calc_max_corr(vec, norm_base_s, norm_base_c):
#     vec_m = vec - np.mean(vec, axis = 1).reshape(-1,1)
#     norm_vec = (vec_m)/np.sqrt(np.sum((vec_m)*(vec_m), axis=1)).reshape(-1,1)
#     # print("norm_base_c", norm_base_c.shape)
#     # print("norm_base_s", norm_base_s.shape)
#     # print("norm_vec", norm_vec.shape)
#     # print("np.dot(norm_base_c, norm_vec.T)", np.dot(norm_base_c, norm_vec.T))
#     # print("np.dot(norm_base_s, norm_vec.T)", np.dot(norm_base_s, norm_vec.T))
#     max_corr_value = np.sqrt(np.power(np.dot(norm_base_c, norm_vec.T), 2) + np.power(np.dot(norm_base_s, norm_vec.T), 2))
#     # print(max_corr_value)
#     max_corr_phase = np.arctan2(np.dot(norm_base_s, norm_vec.T), np.dot(norm_base_c, norm_vec.T))
#     return max_corr_value, max_corr_phase


# def norm_bases(n_dp, n_dp_in_per):
#     base_s = np.sin(np.arange(n_dp)/n_dp_in_per*2*np.pi)
#     base_c = np.cos(np.arange(n_dp)/n_dp_in_per*2*np.pi)
#     base_s_m = base_s - np.mean(base_s)
#     base_c_m = base_c - np.mean(base_c)
#     norm_base_s = (base_s_m)/np.sqrt(np.sum((base_s_m)*(base_s_m)))
#     norm_base_c = (base_c_m)/np.sqrt(np.sum((base_c_m)*(base_c_m)))
#     return norm_base_s, norm_base_c


# def max_corr_pval(num_datapoints, max_corr):
#     """ pvalue of the max Pearson correlations 
#         max corr: the value of max correlation
#         return: cumulative density
#     """
#     n = num_datapoints - 3
#     p = np.power((1 - np.power(max_corr, 2)), n / 2)
#     return p


# def sem_ratio(avg_vector, sem_vector):
#     """ ratio of the avg_vecotr at which the vector reaches the SEM sphere
#         avg_vector: average vector
#         sem_vector: SEM vector
#         return: the ratio of the average vector from the origin to the SEM sphere over the average vector
#     """
   
#     ratio = 1.0 - 1.96 / np.sqrt(np.sum(np.power(avg_vector / sem_vector, 2))) # 1.96 is the 95% confidence interval
#     return max(0, ratio)


# def costest(avg_vec, sem_vec, n_dp, n_dp_in_per):
#     # prepare bases
#     norm_base_s, norm_base_c = norm_bases(n_dp, n_dp_in_per)

#     ## prepare vectors to handle nan
#     avg_vector = avg_vec.copy()
#     sem_vector = sem_vec.copy()
#     # each SEM needs to be >0
#     sem_vector[~(sem_vector>0)] = np.nanmax(sem_vector)
#     # replace nan in SEM with an effectively infinite SEM
#     sem_vector[np.isnan(avg_vector)] = np.nanmax(sem_vector)*1000000
#     # replace nan in AVG with median
#     avg_vector[np.isnan(avg_vector)] = np.nanmedian(avg_vector)
#     # taking the SEM into account
#     sem_r = sem_ratio(avg_vector, sem_vector)

#     # tuple of max-correlation value and the phase of max correlation
#     mc, mc_ph = calc_max_corr(avg_vector, norm_base_s, norm_base_c)

#     adj_mc = mc * sem_r
#     p_org = max_corr_pval(n_dp, mc)
#     p_sem_adj = max_corr_pval(n_dp, adj_mc)
    
#     # max-correlation value, phase of max correlation, original p, SEM adjusted p
#     return mc, mc_ph, p_org, p_sem_adj




import math
def rad2ph(rad):
#     return (int((2*np.pi+rad)*180/np.pi*24/360),  int((rad)*180/np.pi*24/360))[rad>=0]
    if math.isnan(rad):
        return np.nan
    else:
        return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]
    

In [30]:
# cfos_fol="/mnt/data1/yamashitaData1/231012_circadian_2nd_Data1/231012_circadian_2nd_Reconst/"
# exp = "2nd"
pre_root = "/mnt/"

src = pre_root+"/gpu_data/data1/kinoshita/"
dst = pre_root+"/gpu_data/data8/kinoshita_cfos/"


cfos_fol = pre_root+ "/gpu_data/data1//yamashitaData1/230828circadian_Data1/230828circadian_1st_Reconst/"
exp = "1st"
savedir = dst + "/cfos_app/"

CT_li = np.arange(0,48,4)
sample_ids = np.arange(1,7,1)

reconsts = os.listdir(cfos_fol)
sample_names=[]
colors=[]
data_parent_paths=[]
data_moving_paths =[]

for CT in CT_li:
#     if CT<44:
#         continue
    for sample_id in sample_ids:
#         if sample_id >1:
#             continue
        sample = "CT"+str(CT)+"_"+str(sample_id).zfill(2)

        for reconst in reconsts:
#             sample_names.append(("_").join(reconst.split("_")[1:3]))

            if sample in reconst:
                sample_names.append(sample)
                for color in os.listdir(cfos_fol+reconst):
                    if "cfos" in color:
                        data_moving_paths.append(cfos_fol+reconst+"/"+color)
                    else:
                        data_parent_paths.append(cfos_fol+reconst+"/"+color)

print(len(data_parent_paths))   
print(len(data_moving_paths))
print(len(sample_names))

72
72
72


In [31]:
import cfospy
rdir = "/mnt/gpu_data/data1/kinoshita/CUBIC_R_atlas_ver5_scn/"
vx = 50
ca=cfospy.analysis.read_atlas_data(rdir, vx)
# df_allen = pd.read_csv("Allen_ID_all.csv")
acronyms_all = ca.df_allen["acronym"]
ID_all = ca.ID_all #remove root, grey
print(len(ID_all))



voxel_num: 36245880
839


In [6]:
#treat saturated peaks
from scipy.spatial import cKDTree
src = "/home/gpu_data/data1/"
dst = "/home/gpu_data/data7/"
root = src+"yamashitaData1/"
deconv_fs = ["/230828circadian_Data1/230828circadian_1st_Reconst_median_norm_Deconv", "/231012_circadian_2nd_Data1/231012_circadian_2nd_Reconst_median_norm_Deconv"]
postfix = "output_peak2500"
moving_points_paths=[dst + i +"_"+postfix+"/" for i in deconv_fs]
exps = ["1st", "2nd"]


for l, exp in enumerate(exps):
#     if l >0 :
#         continue
    
    moving_points_path=moving_points_paths[l]
    
    
    moving_points_csv_li = os.listdir(moving_points_path)

    for i, sample in enumerate(sample_names):
#         if i>0:
#             continue
#         if sample != "CT0_01" and sample != "CT8_01" and sample != "CT16_01":
#             continue

        for f in moving_points_csv_li:
#             f=f.replace("cfos_", "")
            if sample in f.replace("cfos_", ""):
                fol = f
                break
        print(f)
            
        if os.path.exists(moving_points_path+f+"/coordinates2.csv"):
            print(exp, sample, "coordinates2.csv already exists")
            continue
            
        if not os.path.exists(moving_points_path+f+"/coordinates.csv"):
            print(exp, sample, "coordinates.csv not found")
            continue
        if os.path.exists(moving_points_path+f+"/coordinates_id.csv"):
            df = pd.read_csv(moving_points_path+f+"/coordinates_id.csv")  #x>z
        else:
            df = pd.read_csv(moving_points_path+f+"/coordinates.csv")
            
        print("pre_df_len:", len(df))
        
        df_i = df[df["intensity"]==65535]
        print("saturated:", len(df_i))
        
        
        coords = df_i[['X', 'Y', 'Z']].values
        tree = cKDTree(coords)

        # 各点について隣接点を探す（距離が1以下）
        adjacent_points = []
        for idx in range(len(df_i)):
            indices = tree.query_ball_point(coords[idx], r=1)
        #     indices.remove(idx)  # 自分自身をリストから除外
            adjacent_points.append(indices)


        merged_lists = merge_lists(adjacent_points)
        print(len(merged_lists))

        center_near=[]
        for j, points in enumerate(merged_lists):
        #     if j>0:
        #         continue
            df_c = df_i.iloc[points]
            center = (np.sum(df_c["X"])/len(df_c), np.sum(df_c["Y"])/len(df_c), np.sum(df_c["Z"])/len(df_c))
        #     print(center)

            coords = df_c[['X', 'Y', 'Z']].values
            tree = cKDTree(coords)

            distance, index = tree.query(np.array(center))

        # 結果の表示
            nearest = df_c.iloc[index]
#             print(nearest)
            center_near.append(nearest)


        df_uni = pd.concat(center_near, axis=1).T
        df_uni= df_uni.reset_index()
        
        if "Unnamed: 0" in df_uni.columns:
            df_uni.drop("Unnamed: 0", axis=1)
        if "index" in df_uni.columns:
            df_uni = df_uni.drop("index", axis=1)
        
        if "Unnamed: 0" in df.columns:
            df = df.drop("Unnamed: 0", axis=1)
        df = df[df["intensity"]!=65535]
        df = pd.concat([df, df_uni], axis=0)
        print("new dataframe", len(df))
        df.to_csv(moving_points_path+f+"/coordinates2.csv")
        

saturated: 9458
1404
X                 2882.00
Y                 3450.00
Z                  121.00
intensity        65535.00
deltaI           65516.00
dissimilarity       12.39
Name: 6987, dtype: float64
X                  475.00
Y                 4586.00
Z                  147.00
intensity        65535.00
deltaI           65535.00
dissimilarity       12.05
Name: 63627, dtype: float64
X                 2162.00
Y                 2085.00
Z                  153.00
intensity        65535.00
deltaI           65535.00
dissimilarity       35.32
Name: 29095, dtype: float64
X                 1456.0
Y                 3598.0
Z                  166.0
intensity        65535.0
deltaI           57628.0
dissimilarity       27.4
Name: 102169, dtype: float64
X                 2196.00
Y                 3697.00
Z                  193.00
intensity        65535.00
deltaI           59731.00
dissimilarity       22.11
Name: 145328, dtype: float64
X                 2897.00
Y                 3964.00
Z           

X                 1968.0
Y                 3911.0
Z                  714.0
intensity        65535.0
deltaI           57792.0
dissimilarity       23.9
Name: 2479370, dtype: float64
X                 1963.00
Y                 3997.00
Z                  715.00
intensity        65535.00
deltaI           58617.00
dissimilarity       25.46
Name: 2489021, dtype: float64
X                 1975.00
Y                 3911.00
Z                  716.00
intensity        65535.00
deltaI           58165.00
dissimilarity       20.15
Name: 2495335, dtype: float64
X                 1975.00
Y                 3953.00
Z                  715.00
intensity        65535.00
deltaI           59003.00
dissimilarity       20.79
Name: 2488815, dtype: float64
X                 2063.00
Y                 4068.00
Z                  715.00
intensity        65535.00
deltaI           57314.00
dissimilarity       26.38
Name: 2489324, dtype: float64
X                 1913.00
Y                 3891.00
Z                  716.0

X                 1453.00
Y                 4359.00
Z                  759.00
intensity        65535.00
deltaI           55111.00
dissimilarity       24.28
Name: 3811779, dtype: float64
X                 3115.00
Y                 3709.00
Z                  760.00
intensity        65535.00
deltaI           58350.00
dissimilarity       24.25
Name: 3817659, dtype: float64
X                 2899.00
Y                 4029.00
Z                  760.00
intensity        65535.00
deltaI           56017.00
dissimilarity       27.44
Name: 3818555, dtype: float64
X                 1915.0
Y                 3844.0
Z                  761.0
intensity        65535.0
deltaI           57284.0
dissimilarity       26.9
Name: 3824557, dtype: float64
X                 1935.0
Y                 3774.0
Z                  765.0
intensity        65535.0
deltaI           57731.0
dissimilarity       28.5
Name: 3875555, dtype: float64
X                 1964.00
Y                 3836.00
Z                  766.00
inte

X                 1865.00
Y                 3371.00
Z                  886.00
intensity        65535.00
deltaI           60201.00
dissimilarity       19.59
Name: 5517698, dtype: float64
X                 1908.00
Y                 3435.00
Z                  835.00
intensity        65535.00
deltaI           60354.00
dissimilarity       23.66
Name: 5525796, dtype: float64
X                 1921.00
Y                 3451.00
Z                  836.00
intensity        65535.00
deltaI           60253.00
dissimilarity       24.59
Name: 5534215, dtype: float64
X                 1918.00
Y                 3488.00
Z                  838.00
intensity        65535.00
deltaI           59493.00
dissimilarity       25.59
Name: 5554420, dtype: float64
X                 2233.00
Y                 4296.00
Z                  837.00
intensity        65535.00
deltaI           57975.00
dissimilarity       22.54
Name: 5545995, dtype: float64
X                 1968.00
Y                 3931.00
Z                 

X                 2796.00
Y                 3284.00
Z                 1190.00
intensity        65535.00
deltaI           56589.00
dissimilarity       25.44
Name: 8547412, dtype: float64
X                 3308.00
Y                 4086.00
Z                 1127.00
intensity        65535.00
deltaI           57006.00
dissimilarity       26.78
Name: 8339362, dtype: float64
X                 2891.00
Y                 3248.00
Z                 1129.00
intensity        65535.00
deltaI           57514.00
dissimilarity       24.86
Name: 8365699, dtype: float64
X                  798.00
Y                 3374.00
Z                 1133.00
intensity        65535.00
deltaI           59045.00
dissimilarity       21.89
Name: 8399118, dtype: float64
X                 1856.00
Y                 2715.00
Z                 1134.00
intensity        65535.00
deltaI           60350.00
dissimilarity       26.74
Name: 8408203, dtype: float64
X                 1991.0
Y                 2728.0
Z                 11

...

X                 1683.00
Y                 3026.00
Z                 1640.00
intensity        65535.00
deltaI           58692.00
dissimilarity       28.13
Name: 16572945, dtype: float64
X                 3476.00
Y                 3546.00
Z                 1640.00
intensity        65535.00
deltaI           57960.00
dissimilarity       24.91
Name: 16577684, dtype: float64
X                 3202.00
Y                 3562.00
Z                 1640.00
intensity        65535.00
deltaI           59041.00
dissimilarity       24.84
Name: 16577824, dtype: float64
X                  302.00
Y                 3761.00
Z                 1640.00
intensity        65535.00
deltaI           58181.00
dissimilarity       26.28
Name: 16579579, dtype: float64
X                 2785.00
Y                 4610.00
Z                 1640.00
intensity        65535.00
deltaI           53319.00
dissimilarity       13.14
Name: 16587470, dtype: float64
X                 3138.00
Y                 3204.00
Z            

X                  769.00
Y                 3761.00
Z                 1854.00
intensity        65535.00
deltaI           59776.00
dissimilarity       18.29
Name: 17602565, dtype: float64
X                 3262.00
Y                 3840.00
Z                 1851.00
intensity        65535.00
deltaI           59458.00
dissimilarity       22.69
Name: 18032750, dtype: float64
X                 1793.00
Y                 2876.00
Z                 1855.00
intensity        65535.00
deltaI           58688.00
dissimilarity       29.88
Name: 17610818, dtype: float64
X                  675.00
Y                 2367.00
Z                 1856.00
intensity        65535.00
deltaI           56844.00
dissimilarity       22.81
Name: 17622633, dtype: float64
X                 1115.00
Y                 3561.00
Z                 1856.00
intensity        65535.00
deltaI           58515.00
dissimilarity       27.98
Name: 17625397, dtype: float64
X                 3298.00
Y                 3134.00
Z            

X                  533.00
Y                 3307.00
Z                 1924.00
intensity        65535.00
deltaI           58446.00
dissimilarity       24.77
Name: 18780087, dtype: float64
X                  635.00
Y                 3708.00
Z                 1925.00
intensity        65535.00
deltaI           57829.00
dissimilarity       25.33
Name: 18790931, dtype: float64
X                  641.00
Y                 3769.00
Z                 1925.00
intensity        65535.00
deltaI           59828.00
dissimilarity       24.03
Name: 18791146, dtype: float64
X                 1085.00
Y                 3403.00
Z                 1927.00
intensity        65535.00
deltaI           59108.00
dissimilarity       23.87
Name: 18811141, dtype: float64
X                 2944.00
Y                 3465.00
Z                 1926.00
intensity        65535.00
deltaI           59478.00
dissimilarity       24.58
Name: 18801832, dtype: float64
X                 1785.00
Y                 3315.00
Z            

X                 1616.00
Y                 3993.00
Z                 2053.00
intensity        65535.00
deltaI           49517.00
dissimilarity       19.44
Name: 19550409, dtype: float64
X                   90.00
Y                 3178.00
Z                 2054.00
intensity        65535.00
deltaI           65535.00
dissimilarity       35.66
Name: 19558122, dtype: float64
X                 2268.00
Y                 3924.00
Z                 2053.00
intensity        65535.00
deltaI           51015.00
dissimilarity       23.69
Name: 19550294, dtype: float64
X                  824.00
Y                 2956.00
Z                 2054.00
intensity        65535.00
deltaI           59442.00
dissimilarity       24.82
Name: 19557347, dtype: float64
X                 1684.00
Y                 3953.00
Z                 2054.00
intensity        65535.00
deltaI           50599.00
dissimilarity       23.62
Name: 19559976, dtype: float64
X                  745.00
Y                 2718.00
Z            

X                  775.00
Y                 2923.00
Z                 2177.00
intensity        65535.00
deltaI           60045.00
dissimilarity       18.16
Name: 20440631, dtype: float64
X                 2976.00
Y                 2770.00
Z                 2188.00
intensity        65535.00
deltaI           57939.00
dissimilarity       20.39
Name: 20487653, dtype: float64
X                  856.00
Y                 3428.00
Z                 2190.00
intensity        65535.00
deltaI           59658.00
dissimilarity       24.61
Name: 20505557, dtype: float64
X                  693.00
Y                 3139.00
Z                 2194.00
intensity        65535.00
deltaI           59133.00
dissimilarity       24.81
Name: 20517083, dtype: float64
X                  745.00
Y                 3173.00
Z                 2231.00
intensity        65535.00
deltaI           59781.00
dissimilarity       24.51
Name: 20577256, dtype: float64
X                 2944.00
Y                 3369.00
Z            

In [14]:
#id annotation　before ai prediction

src = "/home/gpu_data/data1/"
dst = "/home/gpu_data/data7/"
root = src+"yamashitaData1/"
deconv_fs = ["/230828circadian_Data1/230828circadian_1st_Reconst_median_norm_Deconv", "/231012_circadian_2nd_Data1/231012_circadian_2nd_Reconst_median_norm_Deconv"]
postfix = "output_peak3750"
moving_points_paths=[dst + i +"_"+postfix+"/" for i in deconv_fs]
exps = ["1st", "2nd"]


# moving_points_csv_li = os.listdir(moving_points_path)

moving_points_csv_pre = "coordinates2.csv"
moving_points_csv = "cell_table_before.csv"

moved_points_csv = "cell_table_after.csv" 
moved_points_id_csv = "coordinates_id.csv" # "cell_table_annot_I.pkl" 
moved_points_annot_pkl = "cell_table_annot_I.pkl" 
combine_points_csv = "cell_table_combine_I.pkl"
combine_points_npy = "cell_table_combine_I"
# combine_points_csv = "cell_combine_intense.npy"
    
rx = 4 #10/2.5
Resized_um=50
ants_dir_name = "ANTsR50"
before_ants_file = "before_ants_{}um_R.tif".format(Resized_um)
tree = scipy.spatial.cKDTree( np.array([
df_atlas_cell["X(um)"].values,
df_atlas_cell["Y(um)"].values,
df_atlas_cell["Z(um)"].values
]).T )
print("[{}] KD Tree Construction completed.".format(os.getpid()))

for l, exp in enumerate(exps):
#     if l == 0:
#         continue
    cell_nums=np.zeros(len(sample_names), dtype="uint64")
    cell_intenses=np.zeros(len(sample_names), dtype="uint64")
    
    moving_points_path=moving_points_paths[l]
    moving_points_csv_li = os.listdir(moving_points_path)

    for i, sample in enumerate(sample_names):
#         if i>0:
#             continue
        if sample != "CT0_01" and sample != "CT8_01" and sample != "CT16_01":
            continue

        for f in moving_points_csv_li:
            if sample in f.replace("cfos_", ""):
                fol = f
                break
                
        print(f)

        pre_cell = pd.read_csv(moving_points_path+f+"/"+moving_points_csv_pre)  #x>z
        cell_nums[i] = len(pre_cell)
        cell_intenses[i] = np.sum(pre_cell["intensity"])
        
#         print(np.max(pre_cell["X"]))
#         print(np.max(pre_cell["Y"]))
#         print(np.max(pre_cell["Z"]))

#         print(pre_cell.iloc[0:2,:])

        pre_cell = pd.DataFrame({                      #Z>X
            "X(um)":(pre_cell["Z"]*rx).astype("float32"),
            "Y(um)":(pre_cell["Y"]*rx).astype("float32"),
            "Z(um)":(pre_cell["X"]*rx).astype("float32"),
        })

        pre_cell.to_csv(moving_points_path+moving_points_csv, index=False, header=True, chunksize=50000,columns=["X(um)","Y(um)","Z(um)"], float_format="%.3f")

        del pre_cell
        gc.collect()


        data_ants_path_p=savedir+exp+"/" + sample +"/" +"SYTOX-G"

        Mapping = mapping_to_atlas(data_atlas_path, ants_dir_name, data_ants_path_p, before_ants_file)
        # ants points transfer 
        moved_points_dir = Mapping.ants_dst_dir +"/"
#         if not os.path.exists(moved_points_dir+moved_points_csv):
        Mapping.run_antsApplyTransformsToPoints(Mapping.prefix_ants, moving_points_path+moving_points_csv, moved_points_dir+moved_points_csv , Mapping.ants_dst_dir)


#         if not os.path.exists(moved_points_dir+combine_points_csv):
        df_moved = pd.read_csv(moved_points_dir+moved_points_csv, skiprows=1, header=None,names=["X(um)","Y(um)","Z(um)"], dtype={"X":np.float32, "Y":np.float32, "Z":np.float32})
    #         X < Z 
        moved_list_x = (df_moved["X(um)"]).values.tolist()
        moved_list_y = (df_moved["Y(um)"]).values.tolist()
        moved_list_z = (df_moved["Z(um)"]).values.tolist()
#         print(np.max(moved_list_x))
#         print(np.max(moved_list_y))
#         print(np.max(moved_list_z))

        temp = df_moved["X(um)"]
        df_moved["X(um)"]= df_moved["Z(um)"]
        df_moved["Z(um)"]= temp
#         print(np.max(df_moved["X(um)"]))
#         print(np.max(df_moved["Y(um)"]))
#         print(np.max(df_moved["Z(um)"]))

        #annotation

        max_distance = 100000
        dist, idx = tree.query( np.array([
          df_moved["X(um)"].values,

          df_moved["Y(um)"].values,
          df_moved["Z(um)"].values,
        ]).T, k=1, eps=0, p=2, distance_upper_bound=max_distance)

        annotated_df = df_atlas_cell.iloc[idx, :]  #X > Z
        annotated_df.to_pickle(moved_points_dir+moved_points_annot_pkl)

#         combine cell table
        pre_cell = pd.read_csv(moving_points_path+f+"/"+moving_points_csv_pre)  #X>Z
        if "Unnamed: 0" in pre_cell.columns:
            pre_cell = pre_cell.drop(["Unnamed: 0"], axis=1)
        if "Unnamed: 0.1" in pre_cell.columns:
            pre_cell = pre_cell.drop(["Unnamed: 0.1"], axis=1)
        pre_cell = pre_cell.reset_index(drop=True)
        annotated_df = annotated_df.reset_index(drop=True)

        pre_cell["ID"] = annotated_df["atlasID"]
        pre_cell.to_csv(moved_points_dir+moved_points_id_csv)
        print(pre_cell.head())
        
#         df_comb = pd.concat([pre_cell, annotated_df], axis=1)

#         print(df_comb)
#         df_comb.to_pickle(moved_points_dir+combine_points_csv)  #X>Z

        
#         df_comb=df_comb[['X(um)', 'Y(um)', 'Z(um)', 'intensity', "atlasID"]].to_numpy()
        
#         np.save(moved_points_dir+combine_points_npy, df_comb)
        
#     np.save(savedir+exp+"/total_cell_nums", cell_nums)
#     np.save(savedir+exp+"/total_cell_intenses", cell_intenses)


t_cells_1 = np.load(savedir+"1st/total_cell_nums.npy")
t_cells_2 = np.load(savedir+"2nd/total_cell_nums.npy")
# print(t_cells_2)
t_cell_T = np.append(t_cells_1, t_cells_2)
print(t_cell_T)
np.save(savedir+"/total_cell_nums", t_cell_T)

[541549] KD Tree Construction completed.
cfos_CT0_01
/home/gpu_data/data8/cfos_app/1st/CT0_01/SYTOX-G/ANTsR50/ already exists
cfos_CT8_01
/home/gpu_data/data8/cfos_app/1st/CT8_01/SYTOX-G/ANTsR50/ already exists
cfos_CT16_01
/home/gpu_data/data8/cfos_app/1st/CT16_01/SYTOX-G/ANTsR50/ already exists
cfos_CT0_01
/home/gpu_data/data8/cfos_app/2nd/CT0_01/SYTOX-G/ANTsR50/ already exists
cfos_CT8_01
/home/gpu_data/data8/cfos_app/2nd/CT8_01/SYTOX-G/ANTsR50/ already exists
cfos_CT16_01
/home/gpu_data/data8/cfos_app/2nd/CT16_01/SYTOX-G/ANTsR50/ already exists


In [19]:
#id annotation　after ai prediction
fprs = [0.5, 5, 2, 1, 0.2, 20, 40]  #5 2,1 // 2 1 0.2
src = "/home/gpu_data/data1/"
dst = "/home/gpu_data/data7/"
root = src+"yamashitaData1/"
deconv_fs = ["/230828circadian_Data1/230828circadian_1st_Reconst_median_norm_Deconv", "/231012_circadian_2nd_Data1/231012_circadian_2nd_Reconst_median_norm_Deconv"]
exps = ["1st", "2nd"]

rx = 4#10/2.5
Resized_um=50
ants_dir_name = "ANTsR50"
# before_ants_file = "before_ants_{}um_R.tif".format(Resized_um)
# tree = scipy.spatial.cKDTree( np.array([
# df_atlas_cell["X(um)"].values,
# df_atlas_cell["Y(um)"].values,
# df_atlas_cell["Z(um)"].values
# ]).T )
# print("[{}] KD Tree Construction completed.".format(os.getpid()))

for fpr in fprs:
    postfix = "output_peak_ratioI_fpr{}".format(fpr)
    moving_points_paths=[dst + i +"_"+postfix+"/" for i in deconv_fs]

    moving_points_csv_pre = "coordinates_ai.csv"
    moving_points_csv = "cell_table_before_ai.csv"

    moved_points_csv = "cell_table_after_ai_fpr{}.csv".format(fpr)
    moved_points_id_csv ="coordinates_ai_id_fpr{}.csv".format(fpr)
    moved_points_annot_pkl = "cell_table_annot_I_ai_fpr{}.pkl".format(fpr) 
    combine_points_csv = "cell_table_combine_I_ai_fpr{}.pkl".format(fpr)
    combine_points_npy = "cell_table_combine_I_ai_fpr{}".format(fpr)
    combine_points_npy_pre = "cell_table_combine_I_ai_pre_fpr{}".format(fpr)
    # combine_points_csv = "cell_combine_intense.npy"

   

    for l, exp in enumerate(exps):
#         if l >0:
#             continue
        cell_nums=np.zeros(len(sample_names), dtype="uint64")
        cell_intenses=np.zeros(len(sample_names), dtype="uint64")

        moving_points_path=moving_points_paths[l]
        moving_points_csv_li = os.listdir(moving_points_path)

        for i, sample in enumerate(sample_names):
#             if i>0:
#                 continue

            for f in moving_points_csv_li:
    #             f=f.replace("cfos_", "")
                if sample in f.replace("cfos_", ""):
                    fol = f
                    break

            print(f)

    #         if os.path.exists(moved_points_dir+combine_points_csv):
    #             continue

#             pre_cell = pd.read_csv(moving_points_path+f+"/"+moving_points_csv_pre)  #x>z
#             pre_cell=pre_cell[pre_cell["predict"]==1]

#             cell_nums[i] = len(pre_cell)
#             cell_intenses[i] = np.sum(pre_cell["intensity"])

#             print(pre_cell.iloc[0:2,:])
#             print("precell pos", len(pre_cell))

#             pre_cell = pd.DataFrame({                      #Z>X
#                 "X(um)":(pre_cell["Z"]*rx).astype("float32"),
#                 "Y(um)":(pre_cell["Y"]*rx).astype("float32"),
#                 "Z(um)":(pre_cell["X"]*rx).astype("float32"),
#             })

#             pre_cell.to_csv(moving_points_path+moving_points_csv, index=False, header=True, chunksize=50000,columns=["X(um)","Y(um)","Z(um)"], float_format="%.3f")

#             del pre_cell
#             gc.collect()


            data_ants_path_p=savedir+exp+"/" + sample +"/" +"SYTOX-G"

            Mapping = mapping_to_atlas(data_atlas_path, ants_dir_name, data_ants_path_p, before_ants_file)
            # ants points transfer 
            moved_points_dir = Mapping.ants_dst_dir +"/"
            post_cell = pd.read_csv(moved_points_dir+moved_points_id_csv)  #x>z
            post_cell=post_cell[post_cell["predict"]==1]
            post_cell=post_cell[post_cell["ID"]!=0]

            cell_nums[i] = len(post_cell)
            cell_intenses[i] = np.sum(post_cell["intensity"])
 
#             Mapping.run_antsApplyTransformsToPoints(Mapping.prefix_ants, moving_points_path+moving_points_csv, moved_points_dir+moved_points_csv , Mapping.ants_dst_dir)


 
#             df_moved = pd.read_csv(moved_points_dir+moved_points_csv, skiprows=1, header=None,names=["X(um)","Y(um)","Z(um)"], dtype={"X":np.float32, "Y":np.float32, "Z":np.float32})
#         #         X < Z 
#             moved_list_x = (df_moved["X(um)"]).values.tolist()
#             moved_list_y = (df_moved["Y(um)"]).values.tolist()
#             moved_list_z = (df_moved["Z(um)"]).values.tolist()

#             temp = df_moved["X(um)"]
#             df_moved["X(um)"]= df_moved["Z(um)"]
#             df_moved["Z(um)"]= temp


#             #annotation

#             max_distance = 100000
#             dist, idx = tree.query( np.array([
#               df_moved["X(um)"].values,

#               df_moved["Y(um)"].values,
#               df_moved["Z(um)"].values,
#             ]).T, k=1, eps=0, p=2, distance_upper_bound=max_distance)

#             annotated_df = df_atlas_cell.iloc[idx, :]  #X > Z
#             annotated_df.to_pickle(moved_points_dir+moved_points_annot_pkl)   #atlas cell coordinate
#             print("annot ", len(annotated_df))

#             pre_cell = pd.read_csv(moving_points_path+f+"/"+moving_points_csv_pre)  #X>Z
#             if "Unnamed: 0" in pre_cell.columns:
#                 pre_cell = pre_cell.drop(["Unnamed: 0"], axis=1)
#             if "Unnamed: 0.1" in pre_cell.columns:
#                 pre_cell = pre_cell.drop(["Unnamed: 0.1"], axis=1)
#             pre_cell = pre_cell.reset_index(drop=True)
#             annotated_df = annotated_df.reset_index(drop=True)

#             pre_cell["ID"] = annotated_df["atlasID"]
#             pre_cell.to_csv(moved_points_dir+moved_points_id_csv)   #all previous cell coordinates
#             print("precell id", len(pre_cell))

#     #         combine cell table
#             pre_cell = pd.read_csv(moving_points_path+f+"/"+moving_points_csv_pre)  #X>Z
#             pre_cell=pre_cell[pre_cell["predict"]==1]
#             pre_cell = pre_cell[["X", "Y", "Z", "intensity"]]*rx

#             if "Unnamed: 0" in pre_cell.columns:
#                 pre_cell = pre_cell.drop(["Unnamed: 0"], axis=1)
#             pre_cell = pre_cell.reset_index(drop=True)
#             annotated_df = annotated_df.reset_index(drop=True)


#             df_comb = pd.concat([pre_cell, annotated_df], axis=1)
#             print("df_comb", len(df_comb))
# #             print(df_comb.head())
#             df_comb.to_pickle(moved_points_dir+combine_points_csv)  #X>Z
    

#             df_comb2=df_comb[['X(um)', 'Y(um)', 'Z(um)', 'intensity', "atlasID"]].to_numpy()
#             np.save(moved_points_dir+combine_points_npy, df_comb2)

#             df_comb2=df_comb[['X', 'Y', 'Z', 'intensity', "atlasID"]].to_numpy()
#             np.save(moved_points_dir+combine_points_npy_pre, df_comb2)

        np.save(savedir+exp+"/total_cell_nums_fpr{}".format(fpr), cell_nums)
        np.save(savedir+exp+"/total_cell_intenses_fpr{}".format(fpr), cell_intenses)

    t_cells_1 = np.load(savedir+"1st/total_cell_nums_fpr{}.npy".format(fpr))
    t_cells_2 = np.load(savedir+"2nd/total_cell_nums_fpr{}.npy".format(fpr))
    # print(t_cells_2)
    t_cell_T = np.append(t_cells_1, t_cells_2)
    print(t_cell_T)
    np.save(savedir+"/total_cell_nums_fpr{}".format(fpr), t_cell_T)

cfos_CT0_01
/home/gpu_data/data8/cfos_app/1st/CT0_01/SYTOX-G/ANTsR50/ already exists
cfos_CT0_02
/home/gpu_data/data8/cfos_app/1st/CT0_02/SYTOX-G/ANTsR50/ already exists
cfos_CT0_03
/home/gpu_data/data8/cfos_app/1st/CT0_03/SYTOX-G/ANTsR50/ already exists
cfos_CT0_04
/home/gpu_data/data8/cfos_app/1st/CT0_04/SYTOX-G/ANTsR50/ already exists
cfos_CT0_05
/home/gpu_data/data8/cfos_app/1st/CT0_05/SYTOX-G/ANTsR50/ already exists
cfos_CT0_06
/home/gpu_data/data8/cfos_app/1st/CT0_06/SYTOX-G/ANTsR50/ already exists
cfos_CT4_01
/home/gpu_data/data8/cfos_app/1st/CT4_01/SYTOX-G/ANTsR50/ already exists
cfos_CT4_02
/home/gpu_data/data8/cfos_app/1st/CT4_02/SYTOX-G/ANTsR50/ already exists
cfos_CT4_03
/home/gpu_data/data8/cfos_app/1st/CT4_03/SYTOX-G/ANTsR50/ already exists
cfos_CT4_04
/home/gpu_data/data8/cfos_app/1st/CT4_04/SYTOX-G/ANTsR50/ already exists
cfos_CT4_05
/home/gpu_data/data8/cfos_app/1st/CT4_05/SYTOX-G/ANTsR50/ already exists
cfos_CT4_06
/home/gpu_data/data8/cfos_app/1st/CT4_06/SYTOX-G/ANTs

cfos_CT12_06
/home/gpu_data/data8/cfos_app/2nd/CT12_06/SYTOX-G/ANTsR50/ already exists
cfos_CT16_01
/home/gpu_data/data8/cfos_app/2nd/CT16_01/SYTOX-G/ANTsR50/ already exists
cfos_CT16_02
/home/gpu_data/data8/cfos_app/2nd/CT16_02/SYTOX-G/ANTsR50/ already exists
cfos_CT16_03
/home/gpu_data/data8/cfos_app/2nd/CT16_03/SYTOX-G/ANTsR50/ already exists
cfos_CT16_04
/home/gpu_data/data8/cfos_app/2nd/CT16_04/SYTOX-G/ANTsR50/ already exists
cfos_CT16_05
/home/gpu_data/data8/cfos_app/2nd/CT16_05/SYTOX-G/ANTsR50/ already exists
cfos_CT16_06
/home/gpu_data/data8/cfos_app/2nd/CT16_06/SYTOX-G/ANTsR50/ already exists
cfos_CT20_01
/home/gpu_data/data8/cfos_app/2nd/CT20_01/SYTOX-G/ANTsR50/ already exists
cfos_CT20_02
/home/gpu_data/data8/cfos_app/2nd/CT20_02/SYTOX-G/ANTsR50/ already exists
cfos_CT20_03
/home/gpu_data/data8/cfos_app/2nd/CT20_03/SYTOX-G/ANTsR50/ already exists
cfos_CT20_04
/home/gpu_data/data8/cfos_app/2nd/CT20_04/SYTOX-G/ANTsR50/ already exists
cfos_CT20_05
/home/gpu_data/data8/cfos_app/

cfos_CT28_05
/home/gpu_data/data8/cfos_app/1st/CT28_05/SYTOX-G/ANTsR50/ already exists
cfos_CT28_06
/home/gpu_data/data8/cfos_app/1st/CT28_06/SYTOX-G/ANTsR50/ already exists
cfos_CT32_01
/home/gpu_data/data8/cfos_app/1st/CT32_01/SYTOX-G/ANTsR50/ already exists
cfos_CT32_02
/home/gpu_data/data8/cfos_app/1st/CT32_02/SYTOX-G/ANTsR50/ already exists
cfos_CT32_03
/home/gpu_data/data8/cfos_app/1st/CT32_03/SYTOX-G/ANTsR50/ already exists
cfos_CT32_04
/home/gpu_data/data8/cfos_app/1st/CT32_04/SYTOX-G/ANTsR50/ already exists
cfos_CT32_05
/home/gpu_data/data8/cfos_app/1st/CT32_05/SYTOX-G/ANTsR50/ already exists
cfos_CT32_06
/home/gpu_data/data8/cfos_app/1st/CT32_06/SYTOX-G/ANTsR50/ already exists
cfos_CT36_01
/home/gpu_data/data8/cfos_app/1st/CT36_01/SYTOX-G/ANTsR50/ already exists
cfos_CT36_02
/home/gpu_data/data8/cfos_app/1st/CT36_02/SYTOX-G/ANTsR50/ already exists
cfos_CT36_03
/home/gpu_data/data8/cfos_app/1st/CT36_03/SYTOX-G/ANTsR50/ already exists
cfos_CT36_04
/home/gpu_data/data8/cfos_app/

cfos_CT44_04
/home/gpu_data/data8/cfos_app/2nd/CT44_04/SYTOX-G/ANTsR50/ already exists
cfos_CT44_05
/home/gpu_data/data8/cfos_app/2nd/CT44_05/SYTOX-G/ANTsR50/ already exists
cfos_CT44_06
/home/gpu_data/data8/cfos_app/2nd/CT44_06/SYTOX-G/ANTsR50/ already exists
cfos_CT0_01
/home/gpu_data/data8/cfos_app/1st/CT0_01/SYTOX-G/ANTsR50/ already exists
cfos_CT0_02
/home/gpu_data/data8/cfos_app/1st/CT0_02/SYTOX-G/ANTsR50/ already exists
cfos_CT0_03
/home/gpu_data/data8/cfos_app/1st/CT0_03/SYTOX-G/ANTsR50/ already exists
cfos_CT0_04
/home/gpu_data/data8/cfos_app/1st/CT0_04/SYTOX-G/ANTsR50/ already exists
cfos_CT0_05
/home/gpu_data/data8/cfos_app/1st/CT0_05/SYTOX-G/ANTsR50/ already exists
cfos_CT0_06
/home/gpu_data/data8/cfos_app/1st/CT0_06/SYTOX-G/ANTsR50/ already exists
cfos_CT4_01
/home/gpu_data/data8/cfos_app/1st/CT4_01/SYTOX-G/ANTsR50/ already exists
cfos_CT4_02
/home/gpu_data/data8/cfos_app/1st/CT4_02/SYTOX-G/ANTsR50/ already exists
cfos_CT4_03
/home/gpu_data/data8/cfos_app/1st/CT4_03/SYTOX-

cfos_CT12_03
/home/gpu_data/data8/cfos_app/2nd/CT12_03/SYTOX-G/ANTsR50/ already exists
cfos_CT12_04
/home/gpu_data/data8/cfos_app/2nd/CT12_04/SYTOX-G/ANTsR50/ already exists
cfos_CT12_05
/home/gpu_data/data8/cfos_app/2nd/CT12_05/SYTOX-G/ANTsR50/ already exists
cfos_CT12_06
/home/gpu_data/data8/cfos_app/2nd/CT12_06/SYTOX-G/ANTsR50/ already exists
cfos_CT16_01
/home/gpu_data/data8/cfos_app/2nd/CT16_01/SYTOX-G/ANTsR50/ already exists
cfos_CT16_02
/home/gpu_data/data8/cfos_app/2nd/CT16_02/SYTOX-G/ANTsR50/ already exists
cfos_CT16_03
/home/gpu_data/data8/cfos_app/2nd/CT16_03/SYTOX-G/ANTsR50/ already exists
cfos_CT16_04
/home/gpu_data/data8/cfos_app/2nd/CT16_04/SYTOX-G/ANTsR50/ already exists
cfos_CT16_05
/home/gpu_data/data8/cfos_app/2nd/CT16_05/SYTOX-G/ANTsR50/ already exists
cfos_CT16_06
/home/gpu_data/data8/cfos_app/2nd/CT16_06/SYTOX-G/ANTsR50/ already exists
cfos_CT20_01
/home/gpu_data/data8/cfos_app/2nd/CT20_01/SYTOX-G/ANTsR50/ already exists
cfos_CT20_02
/home/gpu_data/data8/cfos_app/

...

cfos_CT44_01
/home/gpu_data/data8/cfos_app/2nd/CT44_01/SYTOX-G/ANTsR50/ already exists
cfos_CT44_02
/home/gpu_data/data8/cfos_app/2nd/CT44_02/SYTOX-G/ANTsR50/ already exists
cfos_CT44_03
/home/gpu_data/data8/cfos_app/2nd/CT44_03/SYTOX-G/ANTsR50/ already exists
cfos_CT44_04
/home/gpu_data/data8/cfos_app/2nd/CT44_04/SYTOX-G/ANTsR50/ already exists
cfos_CT44_05
/home/gpu_data/data8/cfos_app/2nd/CT44_05/SYTOX-G/ANTsR50/ already exists
cfos_CT44_06
/home/gpu_data/data8/cfos_app/2nd/CT44_06/SYTOX-G/ANTsR50/ already exists
cfos_CT0_01
/home/gpu_data/data8/cfos_app/1st/CT0_01/SYTOX-G/ANTsR50/ already exists
cfos_CT0_02
/home/gpu_data/data8/cfos_app/1st/CT0_02/SYTOX-G/ANTsR50/ already exists
cfos_CT0_03
/home/gpu_data/data8/cfos_app/1st/CT0_03/SYTOX-G/ANTsR50/ already exists
cfos_CT0_04
/home/gpu_data/data8/cfos_app/1st/CT0_04/SYTOX-G/ANTsR50/ already exists
cfos_CT0_05
/home/gpu_data/data8/cfos_app/1st/CT0_05/SYTOX-G/ANTsR50/ already exists
cfos_CT0_06
/home/gpu_data/data8/cfos_app/1st/CT0_06/

cfos_CT8_06
/home/gpu_data/data8/cfos_app/2nd/CT8_06/SYTOX-G/ANTsR50/ already exists
cfos_CT12_01
/home/gpu_data/data8/cfos_app/2nd/CT12_01/SYTOX-G/ANTsR50/ already exists
cfos_CT12_02
/home/gpu_data/data8/cfos_app/2nd/CT12_02/SYTOX-G/ANTsR50/ already exists
cfos_CT12_03
/home/gpu_data/data8/cfos_app/2nd/CT12_03/SYTOX-G/ANTsR50/ already exists
cfos_CT12_04
/home/gpu_data/data8/cfos_app/2nd/CT12_04/SYTOX-G/ANTsR50/ already exists
cfos_CT12_05
/home/gpu_data/data8/cfos_app/2nd/CT12_05/SYTOX-G/ANTsR50/ already exists
cfos_CT12_06
/home/gpu_data/data8/cfos_app/2nd/CT12_06/SYTOX-G/ANTsR50/ already exists
cfos_CT16_01
/home/gpu_data/data8/cfos_app/2nd/CT16_01/SYTOX-G/ANTsR50/ already exists
cfos_CT16_02
/home/gpu_data/data8/cfos_app/2nd/CT16_02/SYTOX-G/ANTsR50/ already exists
cfos_CT16_03
/home/gpu_data/data8/cfos_app/2nd/CT16_03/SYTOX-G/ANTsR50/ already exists
cfos_CT16_04
/home/gpu_data/data8/cfos_app/2nd/CT16_04/SYTOX-G/ANTsR50/ already exists
cfos_CT16_05
/home/gpu_data/data8/cfos_app/2n

cfos_CT24_05
/home/gpu_data/data8/cfos_app/1st/CT24_05/SYTOX-G/ANTsR50/ already exists
cfos_CT24_06
/home/gpu_data/data8/cfos_app/1st/CT24_06/SYTOX-G/ANTsR50/ already exists
cfos_CT28_01
/home/gpu_data/data8/cfos_app/1st/CT28_01/SYTOX-G/ANTsR50/ already exists
cfos_CT28_02
/home/gpu_data/data8/cfos_app/1st/CT28_02/SYTOX-G/ANTsR50/ already exists
cfos_CT28_03
/home/gpu_data/data8/cfos_app/1st/CT28_03/SYTOX-G/ANTsR50/ already exists
cfos_CT28_04
/home/gpu_data/data8/cfos_app/1st/CT28_04/SYTOX-G/ANTsR50/ already exists
cfos_CT28_05
/home/gpu_data/data8/cfos_app/1st/CT28_05/SYTOX-G/ANTsR50/ already exists
cfos_CT28_06
/home/gpu_data/data8/cfos_app/1st/CT28_06/SYTOX-G/ANTsR50/ already exists
cfos_CT32_01
/home/gpu_data/data8/cfos_app/1st/CT32_01/SYTOX-G/ANTsR50/ already exists
cfos_CT32_02
/home/gpu_data/data8/cfos_app/1st/CT32_02/SYTOX-G/ANTsR50/ already exists
cfos_CT32_03
/home/gpu_data/data8/cfos_app/1st/CT32_03/SYTOX-G/ANTsR50/ already exists
cfos_CT32_04
/home/gpu_data/data8/cfos_app/

cfos_CT40_04
/home/gpu_data/data8/cfos_app/2nd/CT40_04/SYTOX-G/ANTsR50/ already exists
cfos_CT40_05
/home/gpu_data/data8/cfos_app/2nd/CT40_05/SYTOX-G/ANTsR50/ already exists
cfos_CT40_06
/home/gpu_data/data8/cfos_app/2nd/CT40_06/SYTOX-G/ANTsR50/ already exists
cfos_CT44_01
/home/gpu_data/data8/cfos_app/2nd/CT44_01/SYTOX-G/ANTsR50/ already exists
cfos_CT44_02
/home/gpu_data/data8/cfos_app/2nd/CT44_02/SYTOX-G/ANTsR50/ already exists
cfos_CT44_03
/home/gpu_data/data8/cfos_app/2nd/CT44_03/SYTOX-G/ANTsR50/ already exists
cfos_CT44_04
/home/gpu_data/data8/cfos_app/2nd/CT44_04/SYTOX-G/ANTsR50/ already exists
cfos_CT44_05
/home/gpu_data/data8/cfos_app/2nd/CT44_05/SYTOX-G/ANTsR50/ already exists
cfos_CT44_06
/home/gpu_data/data8/cfos_app/2nd/CT44_06/SYTOX-G/ANTsR50/ already exists
cfos_CT0_01
/home/gpu_data/data8/cfos_app/1st/CT0_01/SYTOX-G/ANTsR50/ already exists
cfos_CT0_02
/home/gpu_data/data8/cfos_app/1st/CT0_02/SYTOX-G/ANTsR50/ already exists
cfos_CT0_03
/home/gpu_data/data8/cfos_app/1st/C

cfos_CT8_03
/home/gpu_data/data8/cfos_app/2nd/CT8_03/SYTOX-G/ANTsR50/ already exists
cfos_CT8_04
/home/gpu_data/data8/cfos_app/2nd/CT8_04/SYTOX-G/ANTsR50/ already exists
cfos_CT8_05
/home/gpu_data/data8/cfos_app/2nd/CT8_05/SYTOX-G/ANTsR50/ already exists
cfos_CT8_06
/home/gpu_data/data8/cfos_app/2nd/CT8_06/SYTOX-G/ANTsR50/ already exists
cfos_CT12_01
/home/gpu_data/data8/cfos_app/2nd/CT12_01/SYTOX-G/ANTsR50/ already exists
cfos_CT12_02
/home/gpu_data/data8/cfos_app/2nd/CT12_02/SYTOX-G/ANTsR50/ already exists
cfos_CT12_03
/home/gpu_data/data8/cfos_app/2nd/CT12_03/SYTOX-G/ANTsR50/ already exists
cfos_CT12_04
/home/gpu_data/data8/cfos_app/2nd/CT12_04/SYTOX-G/ANTsR50/ already exists
cfos_CT12_05
/home/gpu_data/data8/cfos_app/2nd/CT12_05/SYTOX-G/ANTsR50/ already exists
cfos_CT12_06
/home/gpu_data/data8/cfos_app/2nd/CT12_06/SYTOX-G/ANTsR50/ already exists
cfos_CT16_01
/home/gpu_data/data8/cfos_app/2nd/CT16_01/SYTOX-G/ANTsR50/ already exists
cfos_CT16_02
/home/gpu_data/data8/cfos_app/2nd/CT16

In [5]:
#make region ID in graph orders

uni_IDs,rev_IDs = ca.get_uni_rIDs()

print(len(uni_IDs))

rdir = "/home/gpu_data/data1/CUBIC_R_atlas_ver5_scn/"
# sum_file =  "summary_CUBIC-Atlas-1-2.csv"
ex_file = "ex_summary.csv"



df_ex = pd.read_csv(rdir + ex_file, index_col=0)
df_ex["rgb_triplet2"] = df_ex["rgb_triplet"].apply(lambda x:np.array(list(map(int, x.strip('[]').split(', '))))/255)


#graph id order
graph_order_ID = df_ex["id"]
uni_IDs_all = [i for i in graph_order_ID if i in uni_IDs]
print("unique all regions", len(uni_IDs_all))

region_colors = [df_ex[df_ex["id"]==rID]["rgb_triplet2"].iloc[0] for rID in uni_IDs_all]

volume_order = np.array([df_ex[df_ex["id"]==rID]["volume"] for rID in uni_IDs_all])
# acronyms = [df_ex[df_ex["id"]==rID]["acronym"] for rID in uni_IDs]

region_order = np.array([df_ex[df_ex["id"]==rID]["acronym"] for rID in uni_IDs_all])
region_order = [i[0] for i in region_order]



df_sum = df_ex[df_ex["id"].isin(uni_IDs_all)].iloc[:,0:6]
# df_sum.drop("Unnamed: 0", axis=0)

df_sum= df_sum.sort_values(by='id', key=lambda x: x.map({v: i for i, v in enumerate(uni_IDs_all)}))


print(df_sum )



KeyboardInterrupt: 

In [22]:
#cell intensity, count
# um=10 #um
fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]

exps = ["1st","2nd"]
image_file = "raw_stacked_norm.tif"
image_file_raw= "raw_stacked.tif"




ants_dir_name = "ANTsR50"

for fpr in fprs:
    op = "_ai_fpr{}".format(fpr)
    moved_points_id_csv ="coordinates_ai_id_fpr{}.csv".format(fpr)  # previous cell cord
    moved_points_annot_pkl = "cell_table_annot_I_ai_fpr{}.pkl".format(fpr)  #atlascell coord
    combine_points_csv = "cell_table_combine_I_ai_fpr{}.pkl".format(fpr)

    for l, exp in enumerate(exps):
        t_cells = np.load(savedir+"{}/total_cell_nums_fpr{}.npy".format(exp, fpr))
        t_intenses = np.load(savedir+"{}/total_cell_intenses_fpr{}.npy".format(exp, fpr))
        for i, sample in enumerate(sample_names):
    #         if i>0:
    #             continue

            moved_points_dir=savedir+exp+"/" + sample +"/" +"SYTOX-G/"+ants_dir_name+"/"


    #         df_comb=pd.read_csv(moved_points_dir+combine_points_csv, index_col=0)
            df_comb=pd.read_pickle(moved_points_dir+combine_points_csv)
            print(df_comb.iloc[0:3, :])

            r_count = np.zeros(len(uni_IDs_all), dtype="uint64") 
            r_intense = np.zeros(len(uni_IDs_all), dtype="float32") 



            for k, rID in enumerate(uni_IDs_all):
    #             if k>0:
    #                 continue
                if ca.smallID_q(rID):
    #                 print(rID, "small region")
                    index = (np.where(df_comb["atlasID"]==rID)[0]) #.tolist()  #get indexes having region ID 
            #                 median = np.nanmedian(conv_data[index])
            #         if len(index)!=0:
                    r_count[k] = len(index)
                    r_intense[k]=np.nansum(np.array(df_comb["intensity"])[index])

                else:
    #                 print(rID, "not small region")
                    child_IDs, child_regions, middle_IDs, middle_regions = ca.get_child_IDs2(rID)
                    index0 = (np.where(df_comb["atlasID"]==rID)[0])
                    if len(index0)!=0:
                        r_count_sum = len(index0)
                        r_intense_sum=np.nansum(np.array(df_comb["intensity"])[index0])
                    else:
                        r_count_sum =0
                        r_intense_sum=0
                    for ch_ID in child_IDs + middle_IDs:
                        index = np.where(df_comb["atlasID"]==ch_ID)[0]#.tolist()  #get indexes having region ID 
            #                 median = np.nanmedian(conv_data[index])
                        if len(index)!=0:
                            r_count_sum += len(index)
                            r_intense_sum += np.nansum(np.array(df_comb["intensity"])[index])
            #         if r_intense_sum!=0:
                    r_count[k] = r_count_sum
                    r_intense[k]=r_intense_sum

            all_count=len(df_comb)
            all_intense = np.sum(df_comb["intensity"])
            mean_intense = np.mean(df_comb["intensity"])


            r_count_dense = ((r_count.reshape(-1,1)/volume_order)[:,0]).astype("float32")
            r_intense_dense = ((r_intense.reshape(-1,1)/volume_order)[:,0]).astype("float32") #/mm3
            r_mean_intense = (r_intense/r_count).astype("float32")
            r_mean_intense= np.nan_to_num(r_mean_intense)


    #         small_IDs = []
    #         for ind in np.unique(df_comb["atlasID"]):
    #             if ind in ca.df_allen["ID"].tolist():
    #                 if ca.smallID_q(ind):
    #                     small_IDs.append(ind)

            del df_comb
            gc.collect()
    #         all_region_intense = np.sum(r_intense)
    #         r_intense_ratio= (r_intense/all_region_intense).astype("float32")


            r_intense_ratio= (r_intense/t_intenses[i]).astype("float32")
            r_intense_ratio_mean= (r_intense/mean_intense).astype("float32")
            r_count_ratio= (r_count/t_cells[i]).astype("float32")

            df_summary = df_sum.copy()
            df_summary["count"] = r_count
            df_summary["intensity"] = r_intense
            df_summary["cell_density"] = r_count_dense
            df_summary["intensity_density"] = r_intense_dense
            df_summary["mean_intensity"] = r_mean_intense
            df_summary["count_ratio"] = r_count_ratio
            df_summary["intensity_ratio"] = r_intense_ratio
            df_summary["intensity_ratio_mean"] = r_intense_ratio_mean

            if not os.path.exists(savedir+exp+"/region_cell_intense{}/".format(op)):
                os.makedirs(savedir+exp+"/region_cell_intense{}/".format(op))
            df_summary.to_csv(savedir+exp+"/region_cell_intense{}/".format(op)+sample+"_"+"region_cell_intensity_summary.csv")
            print(savedir+exp+"/region_cell_intense{}/".format(op)+sample+"_"+"region_cell_intensity_summary.csv")
            #     
    #     df_summary["intensity_ratio"] = r_intense_ratio
            print(df_summary)
    

         X        Y      Z  intensity  Unnamed: 0      X(um)      Y(um)  \
0  12272.0   7992.0   60.0    32092.0    59437492  11982.270   8481.738   
1  12176.0  11304.0   80.0    24100.0    50794909  12482.331  10786.189   
2   8564.0  18024.0  120.0    27876.0    12420710   9329.375  17459.970   

       Z(um)  atlasID  
0  1541.4019        0  
1   849.7531        0  
2  1753.1122        0  


/tmp/ipykernel_498553/3499524728.py:77: RuntimeWarning: invalid value encountered in divide
  r_mean_intense = (r_intense/r_count).astype("float32")


/home/gpu_data/data8/cfos_app/1st/region_cell_intense_ai_fpr0.5/CT0_01_region_cell_intensity_summary.csv
      id    acronym                           node_name  graph_order  \
2    567         CH                            Cerebrum            2   
3    688        CTX                     Cerebral cortex            3   
4    695      CTXpl                      Cortical plate            4   
5    315  Isocortex                           Isocortex            5   
6    184        FRP       Frontal pole, cerebral cortex            6   
..   ...        ...                                 ...          ...   
834  129         V3                     third ventricle         1299   
835  140         AQ                   cerebral aqueduct         1300   
836  145         V4                    fourth ventricle         1301   
837  153        V4r                      lateral recess         1302   
838  164          c  central canal, spinal cord/medulla         1303   

         rgb_triplet      volu

/tmp/ipykernel_498553/3499524728.py:77: RuntimeWarning: invalid value encountered in divide
  r_mean_intense = (r_intense/r_count).astype("float32")


/home/gpu_data/data8/cfos_app/1st/region_cell_intense_ai_fpr0.5/CT0_02_region_cell_intensity_summary.csv
      id    acronym                           node_name  graph_order  \
2    567         CH                            Cerebrum            2   
3    688        CTX                     Cerebral cortex            3   
4    695      CTXpl                      Cortical plate            4   
5    315  Isocortex                           Isocortex            5   
6    184        FRP       Frontal pole, cerebral cortex            6   
..   ...        ...                                 ...          ...   
834  129         V3                     third ventricle         1299   
835  140         AQ                   cerebral aqueduct         1300   
836  145         V4                    fourth ventricle         1301   
837  153        V4r                      lateral recess         1302   
838  164          c  central canal, spinal cord/medulla         1303   

         rgb_triplet      volu

...

/tmp/ipykernel_498553/3499524728.py:77: RuntimeWarning: invalid value encountered in divide
  r_mean_intense = (r_intense/r_count).astype("float32")


/home/gpu_data/data8/cfos_app/2nd/region_cell_intense_ai_fpr40/CT44_04_region_cell_intensity_summary.csv
      id    acronym                           node_name  graph_order  \
2    567         CH                            Cerebrum            2   
3    688        CTX                     Cerebral cortex            3   
4    695      CTXpl                      Cortical plate            4   
5    315  Isocortex                           Isocortex            5   
6    184        FRP       Frontal pole, cerebral cortex            6   
..   ...        ...                                 ...          ...   
834  129         V3                     third ventricle         1299   
835  140         AQ                   cerebral aqueduct         1300   
836  145         V4                    fourth ventricle         1301   
837  153        V4r                      lateral recess         1302   
838  164          c  central canal, spinal cord/medulla         1303   

         rgb_triplet      volu

/tmp/ipykernel_498553/3499524728.py:77: RuntimeWarning: invalid value encountered in divide
  r_mean_intense = (r_intense/r_count).astype("float32")


/home/gpu_data/data8/cfos_app/2nd/region_cell_intense_ai_fpr40/CT44_05_region_cell_intensity_summary.csv
      id    acronym                           node_name  graph_order  \
2    567         CH                            Cerebrum            2   
3    688        CTX                     Cerebral cortex            3   
4    695      CTXpl                      Cortical plate            4   
5    315  Isocortex                           Isocortex            5   
6    184        FRP       Frontal pole, cerebral cortex            6   
..   ...        ...                                 ...          ...   
834  129         V3                     third ventricle         1299   
835  140         AQ                   cerebral aqueduct         1300   
836  145         V4                    fourth ventricle         1301   
837  153        V4r                      lateral recess         1302   
838  164          c  central canal, spinal cord/medulla         1303   

         rgb_triplet      volu

/tmp/ipykernel_498553/3499524728.py:77: RuntimeWarning: invalid value encountered in divide
  r_mean_intense = (r_intense/r_count).astype("float32")


In [23]:
#integrate all samples intensity to one csv


fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]

exps = ["1st", "2nd"]

for fpr in fprs:
    op = "_ai_fpr{}".format(fpr)
    for l, exp in enumerate(exps):
        df_all=[]
        df_all_r=[]
        df_all_rm=[]
        df_all_c=[]
        df_all_c_r=[]

        cols =[]
        for i, sample in enumerate(sample_names):
        #     if i>0:
        #         continue
        #     path = savedir+exp+"/"+sample+"/cfos/"+"region_intensity_summary_conv{}.csv".format(conv)
            path = savedir+exp+"/region_cell_intense{}/".format(op) + sample + "_"+"region_cell_intensity_summary.csv"
            df = pd.read_csv(path)

            df_all.append(df["intensity"])
            df_all_r.append(df["intensity_ratio"])
            df_all_rm.append(df["intensity_ratio_mean"])
            df_all_c.append(df["count"])
            df_all_c_r.append(df["count_ratio"])

            cols.append(sample)

        df_r_intense = pd.concat(df_all, axis=1)
        df_r_intense.columns=cols
        df_r_intense.insert(0,"id",uni_IDs_all)
        df_r_intense.to_csv(savedir+exp+"/"+"region_cell_intensity{}_summary_{}.csv".format(op, exp))

        df_r_intense_r = pd.concat(df_all_r, axis=1)
        df_r_intense_r.columns=cols
        df_r_intense_r.insert(0,"id",uni_IDs_all)
        df_r_intense_r.to_csv(savedir+exp+"/"+"region_cell_intensity{}_ratio_summary_{}.csv".format(op, exp))

        df_r_intense_r = pd.concat(df_all_rm, axis=1)
        df_r_intense_r.columns=cols
        df_r_intense_r.insert(0,"id",uni_IDs_all)
        df_r_intense_r.to_csv(savedir+exp+"/"+"region_cell_intensity{}_ratio_mean_summary_{}.csv".format(op, exp))

        df_r_intense = pd.concat(df_all_c, axis=1)
        df_r_intense.columns=cols
        df_r_intense.insert(0,"id",uni_IDs_all)
        df_r_intense.to_csv(savedir+exp+"/"+"region_cell{}_count_summary_{}.csv".format(op, exp))

        df_r_intense_r = pd.concat(df_all_c_r, axis=1)
        df_r_intense_r.columns=cols
        df_r_intense_r.insert(0,"id",uni_IDs_all)
        df_r_intense_r.to_csv(savedir+exp+"/"+"region_cell{}_count_ratio_summary_{}.csv".format(op, exp))


In [32]:
df = pd.read_excel("TableS7.xlsx")


In [38]:
#cell_count: analytic cosiner test  from Table S4
fpr = 0.5 #, 5, 2, 1, 0.2, 20, 40]

typev = "count_ratio"

exps = ["1st", "2nd"]
CT_li0 = np.arange(0,96,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []

alphas = [0.0375] #np.arange(0.01, 0.1, 0.01)


for alpha in alphas:
#     op="_ai_fpr{}".format(fpr)



#     # CT_mean_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")
#     # CT_se_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")

#     file_name = "region_cell{}_{}_summary".format(op, typev)
    
#     df_r1 = pd.read_csv(savedir+"{}/{}_{}.csv".format("1st", file_name, "1st"))
#     df_r2 = pd.read_csv(savedir+"{}/{}_{}.csv".format("2nd", file_name, "2nd"), index_col=0)
# #     print(df_r2)

#     CT_li2 = np.arange(48,96, 4)

#     new_col=["id"]

#     for CT in CT_li2:
#         for sample_id in sample_ids:
#             new_col.append("CT"+str(CT)+"_"+str(sample_id).zfill(2))

#     df_r2.columns=new_col
#     df = pd.merge(df_r1, df_r2, on='id', how='inner')
#     # df = df_jtk
#     df = df.drop("Unnamed: 0", axis=1) 
#     df0 = df.copy()
   
    


#     if small_only ==True:
#         small_IDs = []
#         for ind in ca.df_allen["ID"]:
#             if ca.smallID_q(ind):
#                 small_IDs.append(ind)

#         df=df[df["id"].isin(small_IDs)]
#         print(len(df))

    # df = df[df["id"]==186]  #LH
    avg_list = []
    se_list = []
    for i in range(df.shape[0]):
        vals = df.iloc[i, 9:(9+12*2*6)].to_numpy(dtype=float)
        tbl = vals.reshape(24, 6)
        avg = tbl.mean(axis=1)
        se = tbl.std(axis=1,ddof=1) / np.sqrt(tbl.shape[1])
        avg_list.append(avg)
        se_list.append(se)
    

    # Batch analysis for multiple time-series
    data_matrix = np.array(avg_list)  # Multiple time-series
    se_matrix = np.array(se_list)  # Corresponding SEMs
    results = batch_costest(data_matrix[:,:], 6, se_matrix, alpha)

    mc, mc_ph, p_org, p_sem_adj =results[:,0],results[:,1],results[:,2],results[:,3]
    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]
    
    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24
    
    
    cos_v_df = pd.DataFrame({"id":df["id"].tolist(),"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})
    
    p_bh_np = np.ones(len(p_sem_adj))
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")
    # bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[~np.isnan(p_sem_adj)],  method="fdr_bh")
    
    p_bh_np[nonan_id] = p_bh_li
    
    cos_v_df.insert(3, "BH.Q", p_bh_np)
    
    
    # print(cos_v_df)
    
    # cos_v_df  = pd.merge(cos_v_df, df, on='id', how='inner')
    cos_v_df  = pd.concat([cos_v_df, df.iloc[:,9:]], axis=1)
    
    cos_v_df = cos_v_df.sort_values("ADJ.P")
    if small_only == False:
        cos_v_df.to_csv(src+"/JTK_results/"+"cos.cell_{}_1st2nd_ai_fpr{}_{}.csv".format(typev, fpr, alpha))
    else:
        cos_v_df.to_csv(src+"/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}_{}.csv".format(typev, fpr, alpha))
        
#     print("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}.csv".format(typev, fpr))
    th = 0.1    
    print(alpha)
    # print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))


/tmp/ipykernel_366080/3109808303.py:562: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


0.0375
393


In [27]:
#cell_count: analytic cosiner test
fpr = 0.5 #, 5, 2, 1, 0.2, 20, 40]

typev = "count"

exps = ["1st", "2nd"]
CT_li0 = np.arange(0,96,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []

alphas = [0.0375]#np.arange(0.01, 0.1, 0.01)


for alpha in alphas:
    op="_ai_fpr{}".format(fpr)



    # CT_mean_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")
    # CT_se_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")

    file_name = "region_cell{}_{}_summary".format(op, typev)
    
    df_r1 = pd.read_csv(savedir+"{}/{}_{}_ex.csv".format("1st", file_name, "1st"))
    df_r2 = pd.read_csv(savedir+"{}/{}_{}_ex.csv".format("2nd", file_name, "2nd"), index_col=0)
#     print(df_r2)

    CT_li2 = np.arange(48,96, 4)

    new_col=["id"]

    for CT in CT_li2:
        for sample_id in sample_ids:
            new_col.append("CT"+str(CT)+"_"+str(sample_id).zfill(2))

    df_r2.columns=new_col
    df = pd.merge(df_r1, df_r2, on='id', how='inner')
    # df = df_jtk
    df = df.drop("Unnamed: 0", axis=1) 
    df0 = df.copy()
   
    


    if small_only ==True:
        small_IDs = []
        for ind in ca.df_allen["ID"]:
            if ca.smallID_q(ind):
                small_IDs.append(ind)

        df=df[df["id"].isin(small_IDs)]
        print(len(df))
    # print(df)

    # df = df[df["id"]==186]  #LH
    avg_list = []
    se_list = []
    for i in range(df.shape[0]):
        vals = df.iloc[i, 1:(1+12*2*6)].to_numpy(dtype=float)
        tbl = vals.reshape(24, 6)
        avg = tbl.mean(axis=1)
        se = tbl.std(axis=1,ddof=1) / np.sqrt(tbl.shape[1])
        avg_list.append(avg)
        se_list.append(se)
    

    # Batch analysis for multiple time-series
    data_matrix = np.array(avg_list)  # Multiple time-series
    se_matrix = np.array(se_list)  # Corresponding SEMs
    results = batch_costest(data_matrix[:,:], 6, se_matrix, alpha)

    mc, mc_ph, p_org, p_sem_adj =results[:,0],results[:,1],results[:,2],results[:,3]
    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]
    
    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24
    
    
    cos_v_df = pd.DataFrame({"id":df["id"].tolist(),"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})
    # print(cos_v_df)
    
    p_bh_np = np.ones(len(p_sem_adj))
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")
    # bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[~np.isnan(p_sem_adj)],  method="fdr_bh")
    
    p_bh_np[nonan_id] = p_bh_li
    
    cos_v_df.insert(3, "BH.Q", p_bh_np)
    
    
    # print(cos_v_df)
    
    cos_v_df  = pd.merge(cos_v_df, df, on='id', how='inner')
    
    cos_v_df = cos_v_df.sort_values("ADJ.P")
    if small_only == False:
        cos_v_df.to_csv(src+"/JTK_results/"+"cos.cell_{}_1st2nd_ai_fpr{}_{}.csv".format(typev, fpr, alpha))
    else:
        cos_v_df.to_csv(src+"/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}_{}.csv".format(typev, fpr, alpha))
        
#     print("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}.csv".format(typev, fpr))
    th = 0.1    
    print(alpha)
    # print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))


642


/tmp/ipykernel_366080/3109808303.py:204: RuntimeWarning: invalid value encountered in divide
  norm_avg = avg_centered / avg_norms
/tmp/ipykernel_366080/3109808303.py:235: RuntimeWarning: invalid value encountered in divide
  ratio_vec = avg_centered[i] / sem_matrix_clean[i]
/tmp/ipykernel_366080/3109808303.py:562: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


0.025
508
642


/tmp/ipykernel_366080/3109808303.py:204: RuntimeWarning: invalid value encountered in divide
  norm_avg = avg_centered / avg_norms
/tmp/ipykernel_366080/3109808303.py:235: RuntimeWarning: invalid value encountered in divide
  ratio_vec = avg_centered[i] / sem_matrix_clean[i]
/tmp/ipykernel_366080/3109808303.py:562: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


0.0375
508


In [22]:
# cell_count ratio: analytic cosiner test
fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]
typev = "count_ratio"

exps = ["1st", "2nd"]
CT_li0 = np.arange(0,96,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []


for fpr in fprs:
    op="_ai_fpr{}".format(fpr)



    # CT_mean_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")
    # CT_se_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")

    file_name = "region_cell{}_{}_summary".format(op, typev)
    
    df_r1 = pd.read_csv(savedir+"{}/{}_{}.csv".format("1st", file_name, "1st"))
    df_r2 = pd.read_csv(savedir+"{}/{}_{}.csv".format("2nd", file_name, "2nd"))
#     print(df_r2)

    CT_li2 = np.arange(48,96, 4)

    new_col=["id"]

    for CT in CT_li2:
        for sample_id in sample_ids:
            new_col.append("CT"+str(CT)+"_"+str(sample_id).zfill(2))

    df_r2.columns=new_col
    df = pd.merge(df_r1, df_r2, on='id', how='inner')
    # df = df_jtk
    df = df.drop("Unnamed: 0", axis=1) 
    df0 = df.copy()
   
    


    if small_only ==True:
        small_IDs = []
        for ind in ca.df_allen["ID"]:
            if ca.smallID_q(ind):
                small_IDs.append(ind)

        df=df[df["id"].isin(small_IDs)]
        print(len(df))

    avg_list = []
    se_list = []
    for i in range(df.shape[0]):
        vals = df.iloc[i, 1:(1+12*2*6)].to_numpy(dtype=float)
        tbl = vals.reshape(24, 6)
        avg = tbl.mean(axis=1)
        se = tbl.std(axis=1,ddof=1) / np.sqrt(tbl.shape[1])
        avg_list.append(avg)
        se_list.append(se)
    

    # Batch analysis for multiple time-series
    data_matrix = np.array(avg_list)  # Multiple time-series
    se_matrix = np.array(se_list)  # Corresponding SEMs
    results = batch_costest(data_matrix[:,:], 6, se_matrix)

    mc, mc_ph, p_org, p_sem_adj =results[:,0],results[:,1],results[:,2],results[:,3]
    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]
    
    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24
    
    
    cos_v_df = pd.DataFrame({"id":df["id"].tolist(),"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})
    
    p_bh_np = np.ones(len(p_sem_adj))
    # bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[~np.isnan(p_sem_adj)],  method="fdr_bh")
    
    p_bh_np[nonan_id] = p_bh_li
    
    cos_v_df.insert(3, "BH.Q", p_bh_np)
    
    
    # print(cos_v_df)
    cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)
    
    cos_v_df = cos_v_df.sort_values("ADJ.P")
    if small_only == False:
        cos_v_df.to_csv(src+"/JTK_results/"+"cos.cell_{}_1st2nd_ai_fpr{}_new.csv".format(typev, fpr))
    else:
        cos_v_df.to_csv(src+"/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}_new.csv".format(typev, fpr))
        
#     print("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}.csv".format(typev, fpr))
    th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
    print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))


642


/mnt/gpu_data/data1/kinoshita/costest.py:205: RuntimeWarning: invalid value encountered in divide
  norm_avg = avg_centered / avg_norms
/mnt/gpu_data/data1/kinoshita/costest.py:236: RuntimeWarning: invalid value encountered in divide
  ratio_vec = avg_centered[i] / sem_matrix_clean[i]
/tmp/ipykernel_360001/3309306527.py:317: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


353
363


In [44]:
#prepare arrays for cell_count statistics for analytic cosiner test   only one exp
fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]
typev = "count"

exp = "2nd"#, "2nd"]
CT_li0 = np.arange(0,48,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []

for fpr in fprs:
    op="_ai_fpr{}".format(fpr)



    # CT_mean_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")
    # CT_se_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")

    file_name = "region_cell{}_{}_summary".format(op, typev)

    df = pd.read_csv(savedir+"{}/{}_{}.csv".format(exp, file_name, exp), index_col=0)
#     df_r2 = pd.read_csv(savedir+"{}/{}_{}.csv".format("2nd", file_name, "2nd"), index_col=0)
# #     print(df_r2)

#     CT_li2 = np.arange(48,96, 4)

#     new_col=["id"]

#     for CT in CT_li2:
#         for sample_id in sample_ids:
#             new_col.append("CT"+str(CT)+"_"+str(sample_id).zfill(2))

#     df_r2.columns=new_col
#     df = pd.merge(df_r1, df_r2, on='id', how='inner')
#     # df = df_jtk
#     df = df.drop("Unnamed: 0", axis=1) 
# #     print(df)


    if small_only ==True:
        small_IDs = []
        for ind in ca.df_allen["ID"]:
            if ca.smallID_q(ind):
                small_IDs.append(ind)

        df=df[df["id"].isin(small_IDs)]
        len(df)



    avg_list = []
    se_list = []
    for i in range(df.shape[0]):
        vals = df.iloc[i, 1:].to_numpy(dtype=float)
        tbl = vals.reshape(12, 6)
        avg = tbl.mean(axis=1)
        se = tbl.std(axis=1,ddof=1) / np.sqrt(tbl.shape[1])
        avg_list.append(avg)
        se_list.append(se)
    

    # Batch analysis for multiple time-series
    data_matrix = np.array(avg_list)  # Multiple time-series
    se_matrix = np.array(se_list)  # Corresponding SEMs
    results = batch_costest(data_matrix[:,:], 6, se_matrix)

    mc, mc_ph, p_org, p_sem_adj =results[:,0],results[:,1],results[:,2],results[:,3]
    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]
    
    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24
    
    
    cos_v_df = pd.DataFrame({"id":df["id"].tolist(),"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})
    
    p_bh_np = np.ones(len(p_sem_adj))
    # bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[~np.isnan(p_sem_adj)],  method="fdr_bh")
    
    p_bh_np[nonan_id] = p_bh_li
    
    cos_v_df.insert(3, "BH.Q", p_bh_np)
    
    
    # print(cos_v_df)
    cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)
    
    cos_v_df = cos_v_df.sort_values("ADJ.P")
    # cos_v_df
    if small_only == False:
        cos_v_df.to_csv(src + "/JTK_results/"+"cos.cell_{}_{}_ai_fpr{}_new.csv".format(typev, exp, fpr))
    else:
        cos_v_df.to_csv(src + "/JTK_results/"+"cos.cell_{}_{}_small_ai_fpr{}_new.csv".format(typev,exp, fpr))
        
    # print("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st_small_ai_fpr{}.csv".format(typev, fpr))
    th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))
    print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))
    per_nums.append(len(cos_v_df[cos_v_df["BH.Q"] < th]))


/tmp/ipykernel_84078/688577634.py:314: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


151
222


In [36]:
ID_all = ca.df_allen["ID"].tolist()

IDs = [i for i in ID_all if i in df["id"].tolist()]
print

Unnamed: 0.1  Unnamed: 0  order   ID                           node_name  \
0               0           0      0  997                                root   
1               1           1      1    8       Basic cell groups and regions   
2               2           2      2  567                            Cerebrum   
3               3           3      3  688                     Cerebral cortex   
4               4           4      4  695                      Cortical plate   
..            ...         ...    ...  ...                                 ...   
834           834         834   1299  129                     third ventricle   
835           835         835   1300  140                   cerebral aqueduct   
836           836         836   1301  145                    fourth ventricle   
837           837         837   1302  153                      lateral recess   
838           838         838   1303  164  central canal, spinal cord/medulla   

    acronym  parent_id  depth_in_tree                 tree  \
0      root        NaN              0                /997/   
1      grey      997.0              1              /997/8/   
2        CH        8.0              2          /997/8/567/   
3       CTX      567.0              3      /997/8/567/688/   
4     CTXpl      688.0              4  /997/8/567/688/695/   
..      ...        ...            ...                  ...   
834      V3       73.0              2         /997/73/129/   
835      AQ       73.0              2         /997/73/140/   
836      V4       73.0              2         /997/73/145/   
837     V4r      145.0              3     /997/73/145/153/   
838       c       73.0              2         /997/73/164/   

     total_voxel_counts (10 um) Unnamed: 8 Unnamed: 9 Unnamed: 10  
0                     506032520        NaN        NaN         NaN  
1                     449594328        NaN        NaN         NaN  
2                     275860156        NaN        NaN         NaN  
3                     221533548        NaN        NaN         NaN  
4                     212625646        NaN        NaN         NaN  
..                          ...        ...        ...         ...  
834                      891188          Y        NaN         NaN  
835                      405256          Y        NaN         NaN  
836                      961246          Y        NaN         NaN  
837                      461680          Y        NaN         NaN  
838                         432          Y        NaN         NaN  

[839 rows x 13 columns]

In [40]:
#prepare arrays for cell_count statistics for analytic cosiner test   only 36 samples (one cycle)
fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]
typev = "count"

exp = "2nd"#, "2nd"]
half = "2"
CT_li0 = np.arange(0,24,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []

fol_name = "only_one_cycle" 

for fpr in fprs:
    op="_ai_fpr{}".format(fpr)



    # CT_mean_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")
    # CT_se_li = np.zeros((region_nums, len(CT_li0)), dtype="float32")

    file_name = "region_cell{}_{}_summary".format(op, typev)

    df = pd.read_csv(savedir+"{}/{}_{}.csv".format(exp, file_name, exp), index_col=0)
    IDs = [i for i in ID_all if i in df["id"].tolist()]
    print(IDs[0:5])
#     df = df.iloc[:,0:]


    if small_only ==True:
        small_IDs = []
        for ind in ca.df_allen["ID"]:
            if ca.smallID_q(ind):
                small_IDs.append(ind)

        df=df[df["id"].isin(small_IDs)]
    



    avg_list = []
    se_list = []
    for i in range(df.shape[0]):
        vals = df.iloc[i, 1:)].to_numpy(dtype=float)
        tbl = vals.reshape(6, 6)
        avg = tbl.mean(axis=1)
        se = tbl.std(axis=1,ddof=1) / np.sqrt(tbl.shape[1])
        avg_list.append(avg)
        se_list.append(se)
    

    # Batch analysis for multiple time-series
    data_matrix = np.array(avg_list)  # Multiple time-series
    se_matrix = np.array(se_list)  # Corresponding SEMs
    results = batch_costest(data_matrix[:,:], 6, se_matrix)

    mc, mc_ph, p_org, p_sem_adj =results[:,0],results[:,1],results[:,2],results[:,3]
    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]
    
    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24
    
    
    cos_v_df = pd.DataFrame({"id":df["id"].tolist(),"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})
    
    p_bh_np = np.ones(len(p_sem_adj))
    # bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[~np.isnan(p_sem_adj)],  method="fdr_bh")
    
    p_bh_np[nonan_id] = p_bh_li
    
    cos_v_df.insert(3, "BH.Q", p_bh_np)
    
    
    # print(cos_v_df)
    cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)
    
    cos_v_df = cos_v_df.sort_values("ADJ.P")

    # cos_v_df = cos_v_df.sort_values("BH.Q")
    # cos_v_df
    os.makedirs(src + "JTK_results/"+fol_name+"/", exist_ok= True)
    if small_only == False:
        cos_v_df.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_exp{}_{}_new.csv".format(typev, exp, half))
    else:
        cos_v_df.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_exp{}_{}_small_new.csv".format(typev, exp, half))
    # if small_only == False:
    #     cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st2nd_ai_36samples_fpr{}.csv".format(typev, fpr))
    # else:
    #     cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_36samples_fpr{}.csv".format(typev, fpr))
        
    # print("/home/gpu_data/data1/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}.csv".format(typev, fpr))
    th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))
    print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))
    # per_nums.append(len(cos_v_df[cos_v_df["BH.Q"] < th]))
    print(cos_v_df["id"])

[567, 688, 695, 315, 184]
               0           1           2           3           4           5
5     122.000000  113.000000   37.000000  123.333333   72.833333   55.833333
6     951.833333  390.333333  180.333333  484.000000  501.833333  212.000000
7    2035.833333  319.500000  186.333333  476.666667  527.833333  240.833333
8     904.000000  173.500000  147.666667  426.666667  341.166667  185.000000
9       2.500000    1.000000    0.333333    2.166667    1.500000    1.500000
..           ...         ...         ...         ...         ...         ...
825    66.166667   70.833333   94.833333   60.666667   68.166667   60.666667
826   842.333333  672.000000  615.000000  676.666667  648.833333  652.000000
827    84.000000   61.500000   73.000000   79.166667   97.333333  106.833333
829    26.000000   21.500000   21.166667   23.666667    6.666667   10.000000
830     0.166667    0.000000    0.000000    0.000000    0.000000    0.000000

[641 rows x 6 columns]


/tmp/ipykernel_84078/688577634.py:314: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


0
50
5         68
6        667
7      52192
8      52196
9      52264
       ...  
825      108
826      129
827      140
829      153
830      164
Name: id, Length: 641, dtype: int64


In [26]:
#combining pvalues   4
from scipy.stats import combine_pvalues
typev = "count"
small_only = True
fol_name = "only_one_cycle" 

df1 = pd.read_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_exp{}_{}_small_new.csv".format(typev, "1st", "1"))
df2 = pd.read_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_exp{}_{}_small_new.csv".format(typev, "1st", "2"))
df3 = pd.read_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_exp{}_{}_small_new.csv".format(typev, "2nd", "1"))
df4 = pd.read_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_exp{}_{}_small_new.csv".format(typev, "2nd", "2"))

com_pvs = []

for n in range(len(df1)):
    pvals = np.array([df1["ADJ.P"].iloc[n], df2["ADJ.P"].iloc[n], df3["ADJ.P"].iloc[n], df4["ADJ.P"].iloc[n] ])
    stat_fisher, p_fisher = combine_pvalues(pvals, method="fisher")
    com_pvs.append(p_fisher)
# print(com_pvs)
nan_id = np.isnan(np.array(com_pvs))
nonan_id = np.where(nan_id==False)[0]
p_bh_np = np.ones(len(com_pvs))
bool_, p_bh_li, _, _ =  multipletests(np.array(com_pvs)[nonan_id],  method="fdr_bh")
p_bh_np[nonan_id] = p_bh_li


df1.insert(6,"COM.P", com_pvs)
df1["BH.Q"] = p_bh_np
df1=df1.drop("Unnamed: 0", axis=1)
df1=df1.drop("ADJ.P", axis=1)

print(df1)

df0 = pd.read_csv(src + "/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}_new.csv".format(typev, fpr))
df0 = (
    df0.set_index('id')
      .loc[df1["id"].tolist()]        # id_list の順に抽出
      .reset_index()       # インデックスを元に戻す
)
df1 = pd.concat([df1.iloc[:,0:8], df0.iloc[:, 10:]],axis=1)

df1 = df1.sort_values("BH.Q")
if small_only == False:
    df1.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_count_1st2nd_one_cycle_combining_p_new.csv")
else:
    df1.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_count_1st2nd_small_one_cycle_combining_p_new.csv")
th = 0.1  
print(len(df1[df1["COM.P"] < th/2]))
print(len(df1[df1["BH.Q"] < th]))

df1

        id acronym                           node_name      BH.Q     COM.P  \
0       68    FRP1               Frontal pole, layer 1  0.335364  0.091561   
1      667  FRP2/3             Frontal pole, layer 2/3  0.658671  0.482682   
2    52192    FRP5               Frontal pole, layer 5  0.714134  0.581349   
3    52196   FRP6a              Frontal pole, layer 6a  0.765102  0.673051   
4    52264   FRP6b              Frontal pole, layer 6b  0.615294  0.378808   
..     ...     ...                                 ...       ...       ...   
636    108    chpl                      choroid plexus  0.660658  0.495494   
637    129      V3                     third ventricle  0.806519  0.735949   
638    140      AQ                   cerebral aqueduct  0.041090  0.002119   
639    153     V4r                      lateral recess  0.596378  0.355032   
640    164       c  central canal, spinal cord/medulla  1.000000       NaN   

      PER        Ph   LAG  max_corr  CT0_01  ...  CT40_03  CT40

id acronym                                          node_name  \
366   186      LH                                   Lateral habenula   
492   679      CS                     Superior central nucleus raphe   
460    12      IF                      Interfascicular nucleus raphe   
545   222      RO                             Nucleus raphe obscurus   
497   238     RPO                               Nucleus raphe pontis   
..    ...     ...                                                ...   
306  1105      IA                     Intercalated amygdalar nucleus   
371   118     PVi  Periventricular hypothalamic nucleus, intermed...   
524   955    LRNm      Lateral reticular nucleus, magnocellular part   
383   133    PVpo  Periventricular hypothalamic nucleus, preoptic...   
640   164       c                 central canal, spinal cord/medulla   

         BH.Q     COM.P   PER        Ph   LAG  CT0_01  CT0_02  ...  CT88_03  \
366  0.009525  0.000023  24.0 -0.677818  21.4     961     767  ...      754   
492  0.009525  0.000030  24.0 -0.930285  20.4     991    1286  ...     1366   
460  0.017269  0.000081  24.0 -0.624386  21.6     296     273  ...      336   
545  0.021791  0.000224  24.0  2.245651   8.6       3       8  ...        1   
497  0.021791  0.000174  24.0 -0.959821  20.3     155     228  ...      186   
..        ...       ...   ...       ...   ...     ...     ...  ...      ...   
306  0.967431  0.962896  24.0 -1.172427  19.5     535     672  ...      632   
371  0.971368  0.968332  24.0 -1.725539  17.4     450     549  ...      512   
524  0.973584  0.972062  24.0 -0.139060  23.5     309     202  ...      372   
383  0.992888  0.992888  24.0 -0.255384  23.0     477     617  ...      479   
640  1.000000       NaN  24.0  2.094395   8.0       0       0  ...        0   

     CT88_04  CT88_05  CT88_06  CT92_01  CT92_02  CT92_03  CT92_04  CT92_05  \
366      770      703      764     1035      669     1056      764     1046   
492     1403     1109     1255     1924      897     1854     1150     1875   
460      323      343      261      354      246      455      305      394   
545        2        3        3        2        3        5       10        4   
497      166      171      210      255       97      254      181      311   
..       ...      ...      ...      ...      ...      ...      ...      ...   
306      489      741      538      381      325      384      343      536   
371      425      423      399      331      226      325      351      244   
524      149      253       82      276      534      215      208      220   
383      388      458      373      285      251      343      402      345   
640        0        0        0        0        0        0        0        0   

     CT92_06  
366     1113  
492     1994  
460      393  
545        6  
497      327  
..       ...  
306      290  
371      324  
524      201  
383      324  
640        0  

[641 rows x 152 columns]

In [27]:
#combining pvalues   2
from scipy.stats import combine_pvalues
fpr =0.5

fol_name = "only_two_cycle" 
os.makedirs(src + "JTK_results/"+fol_name, exist_ok=True)

df1 = pd.read_csv(src + "/JTK_results/"+"cos.cell_{}_{}_small_ai_fpr{}_new.csv".format(typev, "1st", fpr))
df2 = pd.read_csv(src + "/JTK_results/"+"cos.cell_{}_{}_small_ai_fpr{}_new.csv".format(typev, "2nd", fpr))


com_pvs = []

for n in range(len(df1)):
    pvals = np.array([df1["ADJ.P"].iloc[n], df2["ADJ.P"].iloc[n]])
    stat_fisher, p_fisher = combine_pvalues(pvals, method="fisher")
    com_pvs.append(p_fisher)
# print(com_pvs)

nan_id = np.isnan(np.array(com_pvs))
nonan_id = np.where(nan_id==False)[0]
p_bh_np = np.ones(len(com_pvs))
bool_, p_bh_li, _, _ =  multipletests(np.array(com_pvs)[nonan_id],  method="fdr_bh")
p_bh_np[nonan_id] = p_bh_li


df1.insert(6,"COM.P", com_pvs)
df1["BH.Q"] = p_bh_np
df1=df1.drop("Unnamed: 0", axis=1)
df1=df1.drop("ADJ.P", axis=1)

df0 = pd.read_csv(src + "/JTK_results/"+"cos.cell_{}_1st2nd_small_ai_fpr{}_new.csv".format(typev, fpr))
df0 = (
    df0.set_index('id')
      .loc[df1["id"].tolist()]        # id_list の順に抽出
      .reset_index()       # インデックスを元に戻す
)
df1 = pd.concat([df1.iloc[:,0:8], df0.iloc[:, 10:]],axis=1)


df1 = df1.sort_values("BH.Q")
if small_only == False:
    df1.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_count_1st2nd_two_cycle_combining_p_new.csv")
else:
    df1.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_count_1st2nd_small_two_cycle_combining_p_new.csv")


th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
print(len(df1[df1["COM.P"] < th/2]))
print(len(df1[df1["BH.Q"] < th]))
# print(len(df1[df1["BH.Q2"] < th]))

394
422


In [32]:
#prepare arrays for cell_count statistics for analytic cosiner test  combining n in one cycle
fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]
typev = "count"
th = 0.1
exps = ["1st", "2nd"]
CT_li0 = np.arange(0,96,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []
fol_name = "one_cycle_combining_n"


for fpr in fprs:
  
    op="_ai_fpr{}".format(fpr)


    file_name = "region_cell{}_{}_summary".format(op, typev)

    df_r1 = pd.read_csv(savedir+"{}/{}_{}.csv".format("1st", file_name, "1st"))
    df_r2 = pd.read_csv(savedir+"{}/{}_{}.csv".format("2nd", file_name, "2nd"), index_col=0)

    CT_li2 = np.arange(48,96, 4)

    new_col=["id"]


    for CT in CT_li2:
        for sample_id in sample_ids:
            new_col.append("CT"+str(CT)+"_"+str(sample_id).zfill(2))

    df_r2.columns=new_col
    df = pd.merge(df_r1, df_r2, on='id', how='inner')
    # df = df_jtk
    df = df.drop("Unnamed: 0", axis=1) 
#     print(df)


    if small_only ==True:
        small_IDs = []
        for ind in ca.df_allen["ID"]:
            if ca.smallID_q(ind):
                small_IDs.append(ind)

        df=df[df["id"].isin(small_IDs)]
        len(df)



    # CT_mean_li = []
    # CT_se_li = []
    # for i, CT in enumerate(CT_li0):
    #     df_mean = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].mean(axis=1)
    #     df_sem = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].std(axis=1)/np.sqrt(len(sample_ids))

    #     CT_mean_li.append(df_mean)
    #     CT_se_li.append(df_sem)

    CTs =np.arange(0, 24*1,4)
    num_samp=6
    CT_mean_li = np.zeros(len(CTs))
    
    
    # df_i=CT_df[CT_df["BH.Q"]<th]
    ids = df["id"].tolist()
    
    
    print("num of regions:", len(df))
    
    
    df_r_mean = np.zeros((len(df),len(CTs)))
    df_r_se = np.zeros((len(df),len(CTs)))
    for CT_i in range(len(CTs)):
    #         if CT_i>0:
    #             continue
        
        CT_li2 = np.array((df.iloc[:, CT_i*num_samp+1:(CT_i+1)*num_samp+1]))
        print(df.iloc[:, CT_i*num_samp+1:(CT_i+1)*num_samp+1])
        CT_li2 = np.hstack([CT_li2, np.array( (df.iloc[:, CT_i*num_samp+1+6*6:(CT_i+1)*num_samp+1+6*6]))])
        print(df.iloc[:, CT_i*num_samp+1+6*6:(CT_i+1)*num_samp+1+6*6])
        CT_li2 = np.hstack([CT_li2, np.array((df.iloc[:, CT_i*num_samp+1+6*6*2:(CT_i+1)*num_samp+1+6*6*2]))])
        CT_li2 = np.hstack([CT_li2, np.array((df.iloc[:, CT_i*num_samp+1+6*6*3:(CT_i+1)*num_samp+1+6*6*3]))])
        
        
        # print(df.iloc[:, CT_i*num_samp+1+6*6:(CT_i+1)*num_samp+1+6*6])

        print(CT_li2.shape)  
        df_r_mean[:,CT_i] = np.mean(CT_li2, axis=1)
        df_r_se[:,CT_i] = np.std(CT_li2, axis=1)

    # df_r_mean = pd.concat(CT_mean_li, axis=1)
    # df_r_se = pd.concat(CT_se_li, axis=1)
#     print(df_r_mean)


    #periodicity by cell count
    n_dp = 6 #np.ones(len(df_mean))*12
    n_dp_per = 24 #np.ones(len(df_mean))*6
    # mc, mc_ph, p_org, p_sem_adj = costest(df_m_i[0], df_se_i[0], 12, 6)
    mc, mc_ph, p_org, p_sem_adj = costest(np.array(df_r_mean), np.array(df_r_se), n_dp, n_dp_per)

    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]

    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24


    cos_v_df = pd.DataFrame({"id":df["id"],"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})

    p_bh_np = np.ones(len(p_sem_adj))
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")

    p_bh_np[nonan_id] = p_bh_li

    cos_v_df.insert(3, "BH.Q", p_bh_np)


    # print(cos_v_df)
    cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)

    cos_v_df = cos_v_df.sort_values("BH.Q")

    os.makedirs(src + "JTK_results/"+fol_name+"/", exist_ok= True)
    if small_only == False:
        cos_v_df.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_1st2nd_one_cycle_combining_n".format(typev))
    else:
        cos_v_df.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_1st2nd_small_one_cycle_combining_n.csv".format(typev))
        
    print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))
    
    per_nums.append(len(cos_v_df[cos_v_df["BH.Q"] < th]))


num of regions: 641
     CT0_01  CT0_02  CT0_03  CT0_04  CT0_05  CT0_06
5        57     214     101      75      66      98
6       570     912     287     496     877    1031
7       662    1113     410     451    1989    1575
8       252     593     259     119     796     644
9         1       3       0       1       3       0
..      ...     ...     ...     ...     ...     ...
825      40      50      97      72      77      66
826     693     776     717     622    1104     595
827      53      64      20      44      97      53
829      24       8      13       2       3       6
830       0       0       0       0       0       0

[641 rows x 6 columns]
     CT24_01  CT24_02  CT24_03  CT24_04  CT24_05  CT24_06
5         60      128      222      767      142       75
6        879     1426     1368      819      230      765
7       3711     1755     1421     1626      190      698
8       1415      700      711      381      172      270
9          3        5        0        2   

/tmp/ipykernel_102310/688577634.py:267: RuntimeWarning: invalid value encountered in power
  p = np.power((1 - np.power(max_corr, 2)), n / 2)
/tmp/ipykernel_102310/688577634.py:314: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


11
0


In [34]:
#prepare arrays for cell_count statistics for analytic cosiner test  combining n in two cycles
fprs = [0.5]#, 5, 2, 1, 0.2, 20, 40]
typev = "count"
th = 0.1
exps = ["1st", "2nd"]
CT_li0 = np.arange(0,96,4)
# region_nums =len(uni_IDs)
small_only = True
per_nums = []
fol_name = "two_cycle_combining_n"


for fpr in fprs:
  
    op="_ai_fpr{}".format(fpr)


    file_name = "region_cell{}_{}_summary".format(op, typev)

    df_r1 = pd.read_csv(savedir+"{}/{}_{}.csv".format("1st", file_name, "1st"))
    df_r2 = pd.read_csv(savedir+"{}/{}_{}.csv".format("2nd", file_name, "2nd"), index_col=0)

    CT_li2 = np.arange(48,96, 4)

    new_col=["id"]


    for CT in CT_li2:
        for sample_id in sample_ids:
            new_col.append("CT"+str(CT)+"_"+str(sample_id).zfill(2))

    df_r2.columns=new_col
    df = pd.merge(df_r1, df_r2, on='id', how='inner')
    # df = df_jtk
    df = df.drop("Unnamed: 0", axis=1) 
    print(df)


    if small_only ==True:
        small_IDs = []
        for ind in ca.df_allen["ID"]:
            if ca.smallID_q(ind):
                small_IDs.append(ind)

        df=df[df["id"].isin(small_IDs)]
        len(df)



    # CT_mean_li = []
    # CT_se_li = []
    # for i, CT in enumerate(CT_li0):
    #     df_mean = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].mean(axis=1)
    #     df_sem = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].std(axis=1)/np.sqrt(len(sample_ids))

    #     CT_mean_li.append(df_mean)
    #     CT_se_li.append(df_sem)

    CTs =np.arange(0, 24*2,4)
    num_samp=6
    CT_mean_li = np.zeros(len(CTs))
    
    
    # df_i=CT_df[CT_df["BH.Q"]<th]
    ids = df["id"].tolist()
    
    
    print("num of regions:", len(df))
    
    
    df_r_mean = np.zeros((len(df),len(CTs)))
    df_r_se = np.zeros((len(df),len(CTs)))
    for CT_i in range(len(CTs)):
    #         if CT_i>0:
    #             continue
        CT_li2 = np.array((df.iloc[:, CT_i*num_samp+1:(CT_i+1)*num_samp+1]))
        # print(CT_li2)
        CT_li2 = np.hstack([CT_li2,  np.array( df.iloc[:, CT_i*num_samp+1+6*6*2:(CT_i+1)*num_samp+1+6*6*2])])
     
        
        print(CT_li2.shape)
        
        df_r_mean[:,CT_i] = np.mean(CT_li2, axis=1)
        df_r_se[:,CT_i] = np.std(CT_li2, axis=1)

    # df_r_mean = pd.concat(CT_mean_li, axis=1)
    # df_r_se = pd.concat(CT_se_li, axis=1)
#     print(df_r_mean)


    #periodicity by cell count
    n_dp = 12 #np.ones(len(df_mean))*12
    n_dp_per = 12#np.ones(len(df_mean))*6
    # mc, mc_ph, p_org, p_sem_adj = costest(df_m_i[0], df_se_i[0], 12, 6)
    mc, mc_ph, p_org, p_sem_adj = costest(np.array(df_r_mean), np.array(df_r_se), n_dp, n_dp_per)

    nan_id = np.isnan(p_sem_adj)
    nonan_id = np.where(nan_id==False)[0]

    phase_li = list(map(rad2ph, mc_ph))
    acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
    node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
    per_li = np.ones(len(df))*24


    cos_v_df = pd.DataFrame({"id":df["id"],"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})

    p_bh_np = np.ones(len(p_sem_adj))
    bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")

    p_bh_np[nonan_id] = p_bh_li

    cos_v_df.insert(3, "BH.Q", p_bh_np)


    # print(cos_v_df)
    cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)

    cos_v_df = cos_v_df.sort_values("BH.Q")

    os.makedirs(src + "JTK_results/"+fol_name+"/", exist_ok= True)
    if small_only == False:
        cos_v_df.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_1st2nd_two_cycle_combining_n".format(typev))
    else:
        cos_v_df.to_csv(src + "JTK_results/"+fol_name+"/"+"cos.cell_{}_1st2nd_small_two_cycle_combining_n".format(typev))
        
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
    print(th)
    print(len(cos_v_df[cos_v_df["ADJ.P"] < th/2]))
    print(len(cos_v_df[cos_v_df["BH.Q"] < th]))
    per_nums.append(len(cos_v_df[cos_v_df["BH.Q"] < th]))


      id   CT0_01   CT0_02   CT0_03  CT0_04   CT0_05   CT0_06  CT4_01  CT4_02  \
0    567  1056551  1675849  1253739  867054  1552489  1411706  446550  902987   
1    688  1013061  1597958  1197832  823473  1509393  1356987  423256  863245   
2    695   994025  1566536  1167257  807927  1484448  1331199  412528  841904   
3    315   739320  1194912   837340  596638  1203629  1031764  286310  612712   
4    184     1542     2835     1057    1142     3731     3348     187     779   
..   ...      ...      ...      ...     ...      ...      ...     ...     ...   
826  129      693      776      717     622     1104      595     618     857   
827  140       53       64       20      44       97       53      64      62   
828  145       32       14       33       5       21       22      58      55   
829  153       24        8       13       2        3        6      20      11   
830  164        0        0        0       0        0        0       0       0   

     CT4_03  ...  CT88_03  

/tmp/ipykernel_102310/688577634.py:314: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


0.1
321
324


In [47]:
df

id  CT0_01  CT0_02  CT0_03  CT0_04  CT0_05  CT0_06  CT4_01  CT4_02  \
5       68      57     214     101      75      66      98      10      85   
6      667     570     912     287     496     877    1031      43     280   
7    52192     662    1113     410     451    1989    1575      70     264   
8    52196     252     593     259     119     796     644      62     150   
9    52264       1       3       0       1       3       0       2       0   
..     ...     ...     ...     ...     ...     ...     ...     ...     ...   
825    108      40      50      97      72      77      66      60      67   
826    129     693     776     717     622    1104     595     618     857   
827    140      53      64      20      44      97      53      64      62   
829    153      24       8      13       2       3       6      20      11   
830    164       0       0       0       0       0       0       0       0   

     CT4_03  ...  CT88_03  CT88_04  CT88_05  CT88_06  CT92_01  CT92_02  \
5        37  ...       68       38       57       40       44       16   
6       110  ...      660      417      586      213      187       67   
7        77  ...      764      528      732      164      483       48   
8        32  ...      488      384      374      131      401       95   
9         0  ...        0        3        2        3        1        1   
..      ...  ...      ...      ...      ...      ...      ...      ...   
825      80  ...       87       66       67       88       62       71   
826     326  ...      729      659      674      492      626      511   
827      19  ...       79      119       79      118      120      112   
829      11  ...        3        8        8        2        5        7   
830       0  ...        0        0        0        0        0        0   

     CT92_03  CT92_04  CT92_05  CT92_06  
5         25       15      190       45  
6        156      186      478      198  
7        170      149      475      120  
8         94       82      303      135  
9          4        1        1        1  
..       ...      ...      ...      ...  
825       72       63       42       54  
826      810      697      648      620  
827      153      110       70       76  
829        8       18       13        9  
830        0        0        0        0  

[641 rows x 145 columns]

In [48]:
i=0
df.iloc[:, CT_i*num_samp+1:(CT_i+1)*num_samp+1]
df.iloc[:, CT_i*num_samp+1+6*6*2:(CT_i+1)*num_samp+6*6*2]

CT44_01  CT44_02  CT44_03  CT44_04  CT44_05  CT44_06
5        133      141       38       44       71       36
6        454      513      207      325      719      886
7        406      349      359      229      259     2488
8        189      267      119       91      145     1211
9          1        1        1        0        0        5
..       ...      ...      ...      ...      ...      ...
825       64       48       48       45       55      157
826      499      567      763      497      745      588
827      101       80       37       68      109       52
829       10        7        7       31       15       50
830        0        0        0        0        0        0

[641 rows x 6 columns]

In [50]:
df.iloc[:, CT_i*num_samp+1+6*6*2:(CT_i+1)*num_samp+1+6*6*2]

CT92_01  CT92_02  CT92_03  CT92_04  CT92_05  CT92_06
5         44       16       25       15      190       45
6        187       67      156      186      478      198
7        483       48      170      149      475      120
8        401       95       94       82      303      135
9          1        1        4        1        1        1
..       ...      ...      ...      ...      ...      ...
825       62       71       72       63       42       54
826      626      511      810      697      648      620
827      120      112      153      110       70       76
829        5        7        8       18       13        9
830        0        0        0        0        0        0

[641 rows x 6 columns]

In [8]:

if small_only ==True:
    small_IDs = []
    for ind in ca.df_allen["ID"]:
        if ca.smallID_q(ind):
            small_IDs.append(ind)

    df=df[df["id"].isin(small_IDs)]
    len(df)


        
CT_mean_li = []
CT_se_li = []
for i, CT in enumerate(CT_li0):
    df_mean = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].mean(axis=1)
    df_sem = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].std(axis=1)/np.sqrt(len(sample_ids))
    
    CT_mean_li.append(df_mean)
    CT_se_li.append(df_sem)

df_r_mean = pd.concat(CT_mean_li, axis=1)
df_r_se = pd.concat(CT_se_li, axis=1)
print(df_r_mean)


#periodicity by cell count
n_dp = 24 #np.ones(len(df_mean))*12
n_dp_per = 6#np.ones(len(df_mean))*6
# mc, mc_ph, p_org, p_sem_adj = costest(df_m_i[0], df_se_i[0], 12, 6)
mc, mc_ph, p_org, p_sem_adj = costest(np.array(df_r_mean), np.array(df_r_se), n_dp, n_dp_per)

nan_id = np.isnan(p_sem_adj)
nonan_id = np.where(nan_id==False)[0]

phase_li = list(map(rad2ph, mc_ph))
acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
per_li = np.ones(len(df))*24


cos_v_df = pd.DataFrame({"id":df["id"],"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})

p_bh_np = np.ones(len(p_sem_adj))
bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")

p_bh_np[nonan_id] = p_bh_li

cos_v_df.insert(3, "BH.Q", p_bh_np)


# print(cos_v_df)
cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)

cos_v_df = cos_v_df.sort_values("BH.Q")
# cos_v_df
if small_only ==False:
    cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_count_ratio_1st2nd_ai_fpr{}.csv".format(fpr))
else:
    cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_count_ratio_1st2nd_small_ai_fpr{}.csv".format(fpr))
th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
print(len(cos_v_df[cos_v_df["BH.Q"] < th]))

642

In [14]:

        
CT_mean_li = []
CT_se_li = []
for i, CT in enumerate(CT_li0):
    df_mean = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].mean(axis=1)
    df_sem = df.iloc[:, 1+i*len(sample_ids):1+(i+1)*len(sample_ids)].std(axis=1)/np.sqrt(len(sample_ids))
    
    CT_mean_li.append(df_mean)
    CT_se_li.append(df_sem)

df_r_mean = pd.concat(CT_mean_li, axis=1)
df_r_se = pd.concat(CT_se_li, axis=1)
print(df_r_mean)


#periodicity by cell count
n_dp = 24 #np.ones(len(df_mean))*12
n_dp_per = 6#np.ones(len(df_mean))*6
# mc, mc_ph, p_org, p_sem_adj = costest(df_m_i[0], df_se_i[0], 12, 6)
mc, mc_ph, p_org, p_sem_adj = costest(np.array(df_r_mean), np.array(df_r_se), n_dp, n_dp_per)

nan_id = np.isnan(p_sem_adj)
nonan_id = np.where(nan_id==False)[0]

phase_li = list(map(rad2ph, mc_ph))
acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
per_li = np.ones(len(df))*24


cos_v_df = pd.DataFrame({"id":df["id"],"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})

p_bh_np = np.ones(len(p_sem_adj))
bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")

p_bh_np[nonan_id] = p_bh_li

cos_v_df.insert(3, "BH.Q", p_bh_np)


# print(cos_v_df)
cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)

cos_v_df = cos_v_df.sort_values("BH.Q")
# cos_v_df
cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_count_ratio_1st2nd_ai_fpr{}.csv".format(fpr))
th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
print(len(cos_v_df[cos_v_df["BH.Q"] < th]))

           0             1         2             3         4         5   \
0    0.837310  7.693153e-01  0.742982  7.878853e-01  0.794440  0.799328   
1    0.802631  7.260900e-01  0.712518  7.553623e-01  0.757163  0.767303   
2    0.786809  7.053330e-01  0.696433  7.380628e-01  0.738547  0.750526   
3    0.596925  4.643398e-01  0.479395  5.443571e-01  0.529996  0.548578   
4    0.001413  5.372957e-04  0.000354  7.733822e-04  0.001141  0.000855   
..        ...           ...       ...           ...       ...       ...   
832  0.000493  8.640316e-04  0.000977  8.625788e-04  0.000796  0.000513   
833  0.000036  7.655562e-05  0.000170  1.371995e-04  0.000106  0.000066   
834  0.000014  5.742408e-05  0.000119  1.530499e-04  0.000069  0.000075   
835  0.000006  2.304804e-05  0.000055  4.102140e-05  0.000013  0.000019   
836  0.000000  1.832670e-07  0.000000  1.387238e-07  0.000000  0.000000   

           6         7         8         9   ...        14        15  \
0    0.836031  0.782787  0.

In [15]:
#periodicity by cell count
n_dp = 24 #np.ones(len(df_mean))*12
n_dp_per = 6#np.ones(len(df_mean))*6
# mc, mc_ph, p_org, p_sem_adj = costest(df_m_i[0], df_se_i[0], 12, 6)
mc, mc_ph, p_org, p_sem_adj = costest(np.array(df_r_mean), np.array(df_r_se), n_dp, n_dp_per)

nan_id = np.isnan(p_sem_adj)
nonan_id = np.where(nan_id==False)[0]

phase_li = list(map(rad2ph, mc_ph))
acronyms= [ca.df_allen[ca.df_allen["ID"]==rID]["acronym"].iloc[0] for rID in df["id"]]
node_names= [ca.df_allen[ca.df_allen["ID"]==rID]["node_name"].iloc[0] for rID in df["id"]]
per_li = np.ones(len(df))*24


cos_v_df = pd.DataFrame({"id":df["id"],"acronym":acronyms, "node_name":node_names,  "ADJ.P":p_sem_adj,  "PER":per_li, "Ph":mc_ph, "LAG":phase_li, "max_corr":mc,})

p_bh_np = np.ones(len(p_sem_adj))
bool_, p_bh_li, _, _ =  multipletests(p_sem_adj[nonan_id],  method="fdr_bh")

p_bh_np[nonan_id] = p_bh_li

cos_v_df.insert(3, "BH.Q", p_bh_np)


# print(cos_v_df)
cos_v_df  =  pd.concat([cos_v_df, df.iloc[:, 1:]],axis=1)

cos_v_df = cos_v_df.sort_values("BH.Q")
# cos_v_df
cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_count_ratio_1st2nd_ai_fpr{}.csv".format(fpr))
th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
print(len(cos_v_df[cos_v_df["BH.Q"] < th]))

/tmp/ipykernel_641951/688577634.py:239: RuntimeWarning: invalid value encountered in divide
  norm_vec = (vec_m)/np.sqrt(np.sum((vec_m)*(vec_m), axis=1)).reshape(-1,1)
/tmp/ipykernel_641951/688577634.py:314: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  return (round((2*np.pi+rad)*180/np.pi*24/360, 1),  round((rad)*180/np.pi*24/360, 1))[rad>=0]


id   acronym                                          node_name  \
496    286       SCH                            Suprachiasmatic nucleus   
447   1113       IAD          Interanterodorsal nucleus of the thalamus   
107    847     AUDp5                     Primary auditory area, layer 5   
734    125       opt                                        optic tract   
459     51       ILM         Intralaminar nuclei of the dorsal thalamus   
..     ...       ...                                                ...   
803    940      cing                                    cingulum bundle   
365    334      BMAp       Basomedial amygdalar nucleus, posterior part   
169  31582  VISli2/3                 Laterointermediate area, layer 2/3   
316    655     COApl  Cortical amygdalar area, posterior part, later...   
794   1051      tspd                         direct tectospinal pathway   

             BH.Q         ADJ.P   PER        Ph   LAG  max_corr    CT0_01  \
496  4.118193e-08  4.926068e-11  24.0  1.727300   6.6  0.947476  0.001048   
447  3.222129e-07  7.708443e-10  24.0 -0.401622  22.5  0.930808  0.000279   
107  9.332495e-07  3.348982e-09  24.0 -2.103800  16.0  0.919785  0.004144   
734  1.228325e-06  5.877155e-09  24.0  2.827922  10.8  0.915099  0.000107   
459  1.648104e-06  9.857079e-09  24.0  0.515122   2.0  0.910541  0.001307   
..            ...           ...   ...       ...   ...       ...       ...   
803  9.568273e-01  9.533937e-01  24.0 -1.156790  19.6  0.067419  0.000407   
365  9.837074e-01  9.813540e-01  24.0 -2.007343  16.3  0.042368  0.000781   
169  9.901611e-01  9.889767e-01  24.0 -2.602309  14.1  0.032519  0.000304   
316  9.922777e-01  9.922777e-01  24.0  0.641731   2.5  0.027198  0.001752   
794  1.000000e+00           NaN  24.0       NaN   NaN       NaN  0.000000   

     ...   CT88_03   CT88_04   CT88_05   CT88_06   CT92_01   CT92_02  \
496  ...  0.000300  0.000316  0.000332  0.000364  0.000166  0.000369   
447  ...  0.000079  0.000106  0.000098  0.000102  0.000192  0.000079   
107  ...  0.007188  0.006388  0.006074  0.006235  0.006578  0.004465   
734  ...  0.000128  0.000207  0.000171  0.000239  0.000102  0.000211   
459  ...  0.000773  0.001056  0.001124  0.001218  0.001132  0.001089   
..   ...       ...       ...       ...       ...       ...       ...   
803  ...  0.000532  0.000688  0.000321  0.000418  0.000354  0.000562   
365  ...  0.001024  0.001017  0.001255  0.001293  0.000828  0.001275   
169  ...  0.000514  0.000321  0.000287  0.000500  0.000427  0.000408   
316  ...  0.001909  0.002027  0.002553  0.002513  0.001733  0.001666   
794  ...  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

      CT92_03   CT92_04   CT92_05   CT92_06  
496  0.000336  0.000416  0.000270  0.000386  
447  0.000207  0.000097  0.000234  0.000267  
107  0.005528  0.005160  0.004956  0.005885  
734  0.000204  0.000207  0.000125  0.000128  
459  0.001141  0.000964  0.001149  0.001203  
..        ...       ...       ...       ...  
803  0.000688  0.000496  0.000415  0.000776  
365  0.001434  0.001133  0.001139  0.001281  
169  0.000537  0.000260  0.000281  0.000779  
316  0.002337  0.001857  0.002182  0.002233  
794  0.000000  0.000000  0.000000  0.000000  

[837 rows x 153 columns]

In [16]:
cos_v_df.to_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_count_ratio_1st2nd_ai_fpr{}.csv".format(fpr))
th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
print(len(cos_v_df[cos_v_df["BH.Q"] < th]))

In [8]:
cos_v_df=pd.read_csv("/home/gpu_data/data1/JTK_results/"+"cos.cell_count_1st2nd_small_ai.csv")

In [19]:
cos_v_df[cos_v_df["id"]==286]

id acronym                node_name          BH.Q         ADJ.P   PER  \
496  286     SCH  Suprachiasmatic nucleus  9.848323e-07  2.150960e-08  24.0   

           Ph  LAG  max_corr  CT0_01  ...  CT88_03  CT88_04  CT88_05  CT88_06  \
496  1.397623  5.3  0.903591    1343  ...      464      402      439      385   

     CT92_01  CT92_02  CT92_03  CT92_04  CT92_05  CT92_06  
496      241      296      286      346      332      359  

[1 rows x 153 columns]

In [ ]:
plt.hist(cos_v_df["LAG"])

In [17]:
th = 0.1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
print(len(cos_v_df[cos_v_df["BH.Q"] < th]))

#cell intensity ratio mean small -> 468/641    phase0,22  many
#cell intensity ratio small -> 412/641
#cell intensity  small -> 471/641

#cell count ratio small -> 408/641

526

In [ ]:
#calc vol in CUBIC-R atlas

large_ID = [315, 698, 1089, 703, 477, 803, 549, 1097,  313, 771, 354,  512]

for rID in large_ID:
    print(rID)
    child_IDs, child_regions, middle_IDs, middle_regions = ca.get_child_IDs2(rID)
    for m_ID in middle_IDs:
        print(m_ID, ca.df_allen[ca.df_allen["ID"]==m_ID]["acronym"], len(np.where(ca.voxel_ID_order_all==m_ID)[0]))




child_IDs, child_regions, middle_IDs, middle_regions = ca.get_child_IDs2(100)
print(middle_regions)
sum =0 
for ch_ID in child_IDs:
    print(ca.df_allen[ca.df_allen["ID"]==ch_ID]["acronym"], len(np.where(ca.voxel_ID_order_all==ch_ID)[0]))
    sum+=len(np.where(ca.voxel_ID_order_all==ch_ID)[0])
    
print(sum)



In [ ]:

#get voxel counts per ID
vx_count_li = []
for rID in df_ex["id"].tolist():
    if ca.smallID_q(rID):
        vx_count_li.append(len(np.where(img_ID == rID)[0]))

    else:
        child_IDs, child_regions, middle_IDs, middle_regions = ca.get_child_IDs2(rID)
        vx_num = len(np.where(img_ID == rID)[0])
        for ch_ID in child_IDs + middle_IDs:
            vx_num += len(np.where(img_ID == ch_ID)[0])
        vx_count_li.append(vx_num)




In [ ]:

rdir2 = "/home/gpu_data/data1/CUBIC_R_atlas_ver5/"
# sum_file =  "summary_CUBIC-Atlas-1-2.csv"
ex_file = "ex_summary.csv"
vx_f = "Regional_iso_10um_voxel_count.csv"
df_ex = pd.read_csv(rdir + ex_file)
df_vx = pd.read_csv(rdir + vx_f)



In [ ]:


rID_li=[]
rID_non_li=[]
vol_li = []
for rID in df_ex["id"].tolist():
    if rID in df_vx["atlasID"].tolist():
        vol = df_vx[df_vx["atlasID"]==rID]["iso_10um_voxel_count"].iloc[0]/(10**6)  #mm3
        vol_li.append(vol)
        rID_li.append(rID)
    else:
#                 print(rID, "not small region")
        child_IDs, child_regions, middle_IDs, middle_regions = ca.get_child_IDs2(rID)
        vx_num=0
        for ch_ID in child_IDs:
            vx_num += df_vx[df_vx["atlasID"]==ch_ID]["iso_10um_voxel_count"].iloc[0]  
        if vx_num!=0:
            vol = vx_num/(10**6)
            vol_li.append(vol)
            rID_li.append(rID)
        else:
            rID_non_li.append(rID)
            